## 1. File description 




## 0. Import module and setting notebook preferences

### 0.1 Import modules

In [1]:
import src.useful as su
import src.labelling as sl
import src.image as si
import src.model as sm 
import src.webscraping as sw
import src.viz as sv

import sqlite3
import pandas as pd 
import numpy as np
from datetime import datetime, timedelta
from scipy.stats import boxcox

import nltk 
from nltk.corpus import stopwords
from collections import Counter


import plotly.io as pio
import plotly.express as px
import plotly.graph_objs as go
from plotly.subplots import make_subplots

from wordcloud import WordCloud
import matplotlib.pyplot as plt
import seaborn as sns

from pandas_profiling import ProfileReport
# import dtale
# from autoviz import data_cleaning_suggestions


from sklearn.model_selection import train_test_split
from sklearn.preprocessing import OneHotEncoder

import re
import os
from pandarallel import pandarallel
from tqdm import tqdm
from tabulate import tabulate

pandarallel.initialize()
sl.Mypandas.initialize()

INFO: Pandarallel will run on 10 workers.
INFO: Pandarallel will use standard multiprocessing data transfer (pipe) to transfer data between the main process and workers.


/var/folders/p4/gh_zxht10ygcpzccbwwy6rl80000gn/T/ipykernel_18114/3685571981.py:28: DeprecationWarning: `import pandas_profiling` is going to be deprecated by April 1st. Please use `import ydata_profiling` instead.
  from pandas_profiling import ProfileReport


### 0.2 Notebook preferences

In [2]:
# Setting pandas options
pd.options.display.max_columns = None
pd.options.display.float_format = '{:,}'.format

# Setting plotly as dark
pio.templates.default = "plotly_dark"
plotly_kwargs = {'category_orders': {"label": [0, 1, 2, 3]},
                 'color_discrete_sequence': ['#1f77b4', '#EF553B', '#00CC96', '#FECB52']}

# Creating SQL database to store all the data for the project
database = "data/main_database.sqlite"
con = sqlite3.connect(database)

# Setting path to export viz
viz_dir = '/Users/marclamy/Desktop/code/viz/instabot/'

# Creating empty README.md file with all viz links
with open('/Users/marclamy/Desktop/code/viz/README.md', 'w') as f:
    f.write('### Instabot project\n\n')

### 0.3 Load and consolidate the data into a single table


In [3]:
def get_main():
    df_main = sl.load_main()
    df_labels = sl.load_labels()
    
    df_main = df_main.merge(df_labels, how='left', on='username')

    # either fillna, either dropna, depending on the use case, comment/uncomment
    # df_main['label'] = df_main['label'].fillna(-1).astype(int)
    # df_main['label'] = df_main['label'].astype(str)

    df_main = df_main.dropna(subset='label').reset_index(drop=True)
    df_main['label'] = df_main['label'].astype(int)
    df_main['binary_label'] = df_main['label'].apply(lambda x: 1 if x == 3 else x).astype(int)

    # df_main = sl.Mypandas(df_main)


    # df_main = df_main.drop([col for col in df_main.columns if any([f'posts_{x}' in col for x in ['sum', 'min', 'max', 'avg', 'concat']])], axis=1)
    return df_main 

df_main = get_main()
df_main_bu = df_main.copy(deep=True)
df_main.head()

username  \
0       adorable-jade-beluga   
1  hysterical-glistening-bee   
2         little-crafty-mink   
3        gentle-crimson-wolf   
4       festive-uppish-leech   

                                           biography  \
0  ⁣⁣28 🇩🇪 🇪🇸 \nCapricorn 🐐 \nDallas TX📍Outside 🍾...   
1  “Moving at a pace slow for some but fast for o...   
2                                          New Page.   
3                                         • 9/26 💘 •   
4                                       Stay mad bum   

                                  biography_wo_emoji biography_emoji  \
0  ⁣⁣28   \nCapricorn  \nDallas TXOutside \n“Her ...        🇩🇪🇪🇸🚫🍾📍🐐   
1  “Moving at a pace slow for some but fast for o...             ⬇️🚨   
2                                          New Page.                   
3                                          • 9/26  •               💘   
4                                       Stay mad bum                   

   biography_emoji_count  biography_emoji_count_distinct  follow_count  \
0                    6.0                             6.0       3,164.0   
1                    2.0                             2.0         114.0   
2                    0.0                             0.0         204.0   
3                    1.0                             1.0         211.0   
4                    0.0                             0.0           0.0   

   follower_count pronouns           domain  \
0         4,676.0     None  mintyswraps.com   
1            52.0     None      youtube.com   
2           422.0     None             None   
3           586.0     None             None   
4             0.0     None             None   

                                             comment  \
0                      Bucks finna have a repeat 🏆 👀   
1                       CRAZY EYES GOT MOVES LOL 🤣🤣😭   
2                        Flight is gonna be heated 😂   
3  Someone forgot to tell the warriors they had a...   
4                      Klay is back scary hoursss 🤪🤪   

                                    comment_wo_emoji comment_emoji  \
0                          Bucks finna have a repeat            👀🏆   
1                           CRAZY EYES GOT MOVES LOL            🤣😭   
2                          Flight is gonna be heated             😂   
3  Someone forgot to tell the warriors they had a...             😂   
4                         Klay is back scary hoursss             🤪   

   comment_emoji_count  comment_emoji_count_distinct  comment_time_difference  \
0                    2                             2                       95   
1                    3                             2                      250   
2                    1                             1                      310   
3                    1                             1                      180   
4                    2                             1                      245   

   comment_likes  post_count  video_count  highlight_reel_count  \
0            967        76.0          6.0                   8.0   
1           1024         0.0          2.0                   0.0   
2            711         0.0          0.0                   0.0   
3            161         6.0          0.0                   0.0   
4            166         0.0          0.0                   0.0   

   hide_like_and_view_counts  has_guides  has_clips  is_private  \
0                        0.0         0.0        1.0         0.0   
1                        0.0         0.0        1.0         0.0   
2                        1.0         0.0        0.0         1.0   
3                        0.0         0.0        0.0         0.0   
4                        0.0         0.0        0.0         1.0   

   is_embeds_disabled  is_joined_recently  is_professional_account  \
0                 0.0                 0.0                      0.0   
1                 0.0                 0.0                      1.0   
2                 0.0                 0.0                      0.0  

In [4]:
pd.read_sql_query('select * from comments', con).shape

(134465, 12)

### 0.3 Split data for the steps that will need feature engineering without introducint data leakage

In [5]:
X = df_main.drop('label', axis=1)
y = df_main['label']
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=42)

In [6]:
os.system('say "error"')

0

In [7]:
# serie = [x for x in enumerate(range(df_main['follow_count'].min() // 100, df_main['follow_count'].max() // 100))]
# serie =

# for value in range()

# serie

### 0.4 Counting labels

In [8]:
unique_comments = df_main.shape[0]
unique_usernames = df_main.drop_duplicates(subset='username').shape[0]

labels = df_main['label'].value_counts()
labels_unique = df_main.drop_duplicates(subset='username')['label'].value_counts()


print(f'{unique_comments = }')
print(f'{unique_usernames = }\n')
print(f'Labels for comment \n{labels}\n')
print(f'Labels unique users \n{labels_unique}\n\n')
print(f'% comments labelled: {sum(labels)/unique_comments:.1%}')
print(f'% users labelled: {sum(labels_unique)/unique_usernames:.1%}')

unique_comments = 30420
unique_usernames = 14571

Labels for comment 
0    18553
1    10928
3      939
Name: label, dtype: int64

Labels unique users 
0    11225
1     2863
3      483
Name: label, dtype: int64


% comments labelled: 100.0%
% users labelled: 100.0%


## 1.0 Quick viz - Move this to part 2 for when the data is clean

### 1.X Pandas profiling

In [9]:
# Generate report of the data
# profile = ProfileReport(df_main, title="Pandas Profiling Report")
# profile.to_file('data/pandas_profiling.html')

In [10]:
df_main.head()

username  \
0       adorable-jade-beluga   
1  hysterical-glistening-bee   
2         little-crafty-mink   
3        gentle-crimson-wolf   
4       festive-uppish-leech   

                                           biography  \
0  ⁣⁣28 🇩🇪 🇪🇸 \nCapricorn 🐐 \nDallas TX📍Outside 🍾...   
1  “Moving at a pace slow for some but fast for o...   
2                                          New Page.   
3                                         • 9/26 💘 •   
4                                       Stay mad bum   

                                  biography_wo_emoji biography_emoji  \
0  ⁣⁣28   \nCapricorn  \nDallas TXOutside \n“Her ...        🇩🇪🇪🇸🚫🍾📍🐐   
1  “Moving at a pace slow for some but fast for o...             ⬇️🚨   
2                                          New Page.                   
3                                          • 9/26  •               💘   
4                                       Stay mad bum                   

   biography_emoji_count  biography_emoji_count_distinct  follow_count  \
0                    6.0                             6.0       3,164.0   
1                    2.0                             2.0         114.0   
2                    0.0                             0.0         204.0   
3                    1.0                             1.0         211.0   
4                    0.0                             0.0           0.0   

   follower_count pronouns           domain  \
0         4,676.0     None  mintyswraps.com   
1            52.0     None      youtube.com   
2           422.0     None             None   
3           586.0     None             None   
4             0.0     None             None   

                                             comment  \
0                      Bucks finna have a repeat 🏆 👀   
1                       CRAZY EYES GOT MOVES LOL 🤣🤣😭   
2                        Flight is gonna be heated 😂   
3  Someone forgot to tell the warriors they had a...   
4                      Klay is back scary hoursss 🤪🤪   

                                    comment_wo_emoji comment_emoji  \
0                          Bucks finna have a repeat            👀🏆   
1                           CRAZY EYES GOT MOVES LOL            🤣😭   
2                          Flight is gonna be heated             😂   
3  Someone forgot to tell the warriors they had a...             😂   
4                         Klay is back scary hoursss             🤪   

   comment_emoji_count  comment_emoji_count_distinct  comment_time_difference  \
0                    2                             2                       95   
1                    3                             2                      250   
2                    1                             1                      310   
3                    1                             1                      180   
4                    2                             1                      245   

   comment_likes  post_count  video_count  highlight_reel_count  \
0            967        76.0          6.0                   8.0   
1           1024         0.0          2.0                   0.0   
2            711         0.0          0.0                   0.0   
3            161         6.0          0.0                   0.0   
4            166         0.0          0.0                   0.0   

   hide_like_and_view_counts  has_guides  has_clips  is_private  \
0                        0.0         0.0        1.0         0.0   
1                        0.0         0.0        1.0         0.0   
2                        1.0         0.0        0.0         1.0   
3                        0.0         0.0        0.0         0.0   
4                        0.0         0.0        0.0         1.0   

   is_embeds_disabled  is_joined_recently  is_professional_account  \
0                 0.0                 0.0                      0.0   
1                 0.0                 0.0                      1.0   
2                 0.0                 0.0                      0.0  

### 1.X dtale

In [11]:
# dtale.show(df_main)

### 1.x Autoviz

In [12]:
os.system('say "auto viz done"')

0

## 1.0 Data cleaning and Univariate Analysis

For the following: 
* Clean the column 
    * Remove missing value/add a missing flag column
    * Flag and remove outliers
* Add new features
* Data viz
    * Look at the distribution for each label
    * Look at describe per label 
    * Next to the title, add - Done / - missing markdown
---


Sub groups of 1.0 with: 
* Biography 
    * bio/bio wo emoji 
    * bio emoji count 
* Comment 
    * Comment/wo emoji
    * Comment int cols 
* Follow/er count 
* Domain
* Post/video count 
    * and highlight_reel_count
* Binary
    * hide like and view count 
    * has guides 
    * has clips 
    * is private 
    * is embeds 
    * is joined 
    * is verified
* Professional/business account 
* Posts list
* Dates diff 


### 1.0.1 Functions - add in my pandas or src files?

In [13]:
df_main['outlier'] = ''
def print_outliers(df, col, threshold=None):
    '''Calculating outliers and flagging them'''
    lower_bound, upper_bound = df.outliers_bound(col)
    df['outlier'] = df.apply(lambda x: x['outlier'] if lower_bound < x[col] < upper_bound else x['outlier'] + ', ' + col, axis=1)
    print(f'Lower bound: {lower_bound} - Upper bound: {upper_bound}\n')
    print(df.query(f'{col} >= @upper_bound').shape[0], 'outliers found\n')

    # Checking outliers per label 
    for label in (0, 1, 3):
        print(f'Label: {label}')
        display(df.query(f'label == {label}')[col].apply(lambda x: lower_bound <= x <= upper_bound).value_counts().reset_index().rename(columns={'index': 'Condition', col: 'Count'}).assign(Percentage=lambda x: (x['Count']/x['Count'].sum()*100).round(1)))
    
    return df

In [14]:
def split_value_count(df, col, label=None):
    if label != None: 
        df = df.query(f'label == {label}')
    # print(df.shape, label)
    val_count = df[col].value_counts().sort_index()
    no = val_count[0] if 0 in val_count.index else 0
    yes = val_count[1] if 1 in val_count.index else 0
    no_norm = (no / (yes + no) * 100).round(2) 
    yes_norm = (yes / (yes + no) * 100).round(2)
    return yes, no, yes_norm, no_norm


def plot_binary_distribution_by_label(df, col, title=None):
    if title == None: 
        f'Distribution of {col.title()} by Labels'
        
    labels = df['label'].unique()

    # create a dictionary to map label to subplot index
    label_subplot_dict = {label: i+1 for i, label in enumerate(labels)}

    # create figure with 2 rows and 3 columns (top chart uses 3 columns)
    fig = make_subplots(rows=2, cols=len(labels), 
                    specs=[[None] + [{'rowspan': 1, 'colspan': 1}] + [None],
                        [{'rowspan': 1, 'colspan': 1} for label in labels]],
                        subplot_titles=['All Labels'] + [f'Label {label}' for label in labels],
                    x_title='Your master x-title',
                    y_title='Your master y-title', 
                    shared_yaxes=True)


    # Adding all data regardless of label
    yes, no, yes_norm, no_norm = split_value_count(df, col)
    fig.add_trace(go.Bar(name='All Labels', 
                            x=df[col].astype(str).sort_values().unique(), 
                            y=[no_norm, yes_norm], 
                            text=[no_norm, yes_norm]), 
                    row=1, col=2)
    

    subplot_titles=[f'All Labels: n={no:,} / y={yes:,}']
    # label subplots
    for label in df['label'].unique():
        yes, no, yes_norm, no_norm = split_value_count(df, col, label)
        subplot_titles.append(f'Label {label} - n={no:,} / y={yes:,}')

        # Adding trace for label
        fig.add_trace(go.Bar(name=f'Label {label}', 
                            x=df[col].astype(str).sort_values().unique(), 
                            y=[no_norm, yes_norm], 
                            text=[no_norm, yes_norm]), 
                                
                        row=2, col=label_subplot_dict[label])

    fig.update_layout(height=800, 
                      title=title)
    
    subplot_titles += [''] + [''] # This is for the x and y main axis titles
    fig.update_layout(annotations=[{'text': name} for name in subplot_titles])

    return fig

### 1.1 Comments - Done ✅

#### 1.1.0 Gram functions

Creating functions to clean/calculate/show different grams of the comments. Will be reusing them for biography.

In [15]:
def clean_and_tokenize(biographies):
    """
    Given a list of biographies, this function performs the following steps:
    1. Remove unwanted characters from each biography
    2. Tokenize the cleaned text into words
    3. Remove stop words from the tokenized text
    4. Return the filtered list of tokens

    Parameters:
    biographies (list): List of strings representing the biographies

    Returns:
    filtered (list): List of lists of filtered tokens
    """
    # Remove unwanted characters
    cleaned = [re.sub(r'[^\w\s\d]', '', b).lower() for b in biographies]
    # Tokenize the text
    tokenized = [nltk.tokenize.word_tokenize(b) for b in cleaned]
    # Remove stop words
    stop_words = set(stopwords.words("english"))
    filtered = [[w for w in t if w.lower() not in stop_words or w.isdigit()] for t in tokenized]
    return filtered
    

def most_frequent_grams(tokens, grams):
    bigrams = [', '.join(b) for t in tokens for b in list(nltk.ngrams(t, grams))]
    most_frequent = dict(Counter(bigrams))
    return most_frequent


def calculate_grams(df, column, max_gram_degree):
    df_grams = pd.DataFrame(columns=['gram', 'count', 'label', 'gram_degree'])
    for label in (0, 1, 2, 3):
        tokens = clean_and_tokenize(df.query(f'label == {label}')[column])
        for gram in (1, 2, 3, 4):
            top_tokens = most_frequent_grams(tokens, gram)
            # top_tokens = {i:[j] for i, j in top_tokens.items()}
            # df_top_tokens = pd.DataFrame(top_tokens, columns=[f'label_{label}_gram_{gram}', f'label_{label}_count_{gram}'])
            current_df = pd.DataFrame(top_tokens.items(), columns=['gram', 'count'])
            current_df['gram_degree'] = gram
            current_df['label'] = label
            df_grams = pd.concat([df_grams, current_df], axis=0)
    return df_grams


def keep_top_n_grams(df, n):
    df_grams_grouped = df.query('label in (0, 1, 3)').sort_values(by=['label', 'gram_degree', 'count'], ascending=[True, True, False])
    df_grams_grouped['row_number'] = df_grams_grouped.groupby(['label', 'gram_degree']).cumcount() + 1
    grams_to_keep = df_grams_grouped.query('row_number <= @n')['gram'].unique().tolist()
    df = df.query('gram in @grams_to_keep').sort_values(['label', 'gram_degree', 'count'], ascending=[True, True, False])
    return df



def plot_grams(df): 
    for degree in df.gram_degree.unique(): 
        fig = px.bar(
            df.query('gram_degree == @degree'), 
            x='gram', 
            y='count', 
            color='label', 
            # barmode='group', 
            **plotly_kwargs,
            title=f'Most grams by label and degree {degree}')
        fig.update_xaxes(tickangle=-90)
        # fig.update_layout(xaxis={'categoryorder':'total descending'})
        
        return fig

#### 1.1.1 Wordcloud

* ????????????????????               Both legit and other bots have the word "first", but not for the same reason. For the legits, its only to be first to comment where for the bots it's the first who read out to them. Let's check the average sentence length where first is in. 

In [16]:
# # Plot wordcloud
# for label in (0, 1, 3):
#     print(f'Label: {label}')
#     wordcloud = WordCloud(width=1800, 
#                           height=1200, 
#                           min_font_size=1, 
#                           max_words=500, 
#                           colormap='tab10')
                          
#     word_list = ' '.join([word for list in df_main.query(f'label == {label}')['comment_wo_emoji'].str.split(' ') for word in list])
#     wordcloud.generate(word_list)

#     plt.figure()
#     plt.imshow(wordcloud, interpolation="bilinear")
#     plt.axis("off")
#     plt.savefig(f'{viz_dir}/wordcloud_comment_{label}.png', dpi=300, pad_inches=0.0, bbox_inches='tight')
#     plt.show()

#### 1.1.2 Calculating bi/tri/quad grams

In [17]:
sub_df = df_main.loc[:, ['comment_wo_emoji', 'label']].drop_duplicates()
df_bio_grams = calculate_grams(sub_df, 'comment_wo_emoji', 20)
df_bio_grams = keep_top_n_grams(df_bio_grams, 30)
# sv.save_plotly_fig(plot_grams(df_bio_grams))

#### 1.1.3 Feature engineering
For each comment, count how many of the top 30 grams to they have

In [18]:
# Adding tri/quad grams count to main df
bots_triquadgrams = df_bio_grams.query('label > 0 and gram_degree > 2').gram.unique().tolist()

def count_grams(text, grams):
    count = 0
    for gram in grams:
        gram = gram.split(',')
        if all(word in text for word in gram):
            count += 1
    return count


df_main['comment_grams_count'] = df_main['comment_wo_emoji'].apply(lambda x: count_grams(x, bots_triquadgrams))

print('% of each label having at least one tri/quad gram')
for label in (0, 1, 3): 
    current_df = df_main.query(f'label == {label}')['comment_grams_count'] > 0
    current_df = current_df.value_counts(normalize=True)
    display(current_df.to_frame(name=f'Label: {label}').round(3))

% of each label having at least one tri/quad gram


Label: 0
False     0.999
True      0.001

Label: 1
False     0.966
True      0.034

Label: 3
False     0.637
True      0.363

In [19]:
# Adding comment length and word count
df_main['comment_length'] = df_main['comment'].str.len()
df_main['comment_word_count'] = df_main['comment'].str.count(' ') + 1

# Dropping columns
df_main = df_main.drop(columns=['comment', 'comment_wo_emoji'])
df_main.head(1)

username                                          biography  \
0  adorable-jade-beluga  ⁣⁣28 🇩🇪 🇪🇸 \nCapricorn 🐐 \nDallas TX📍Outside 🍾...   

                                  biography_wo_emoji biography_emoji  \
0  ⁣⁣28   \nCapricorn  \nDallas TXOutside \n“Her ...        🇩🇪🇪🇸🚫🍾📍🐐   

   biography_emoji_count  biography_emoji_count_distinct  follow_count  \
0                    6.0                             6.0       3,164.0   

   follower_count pronouns           domain comment_emoji  \
0         4,676.0     None  mintyswraps.com            👀🏆   

   comment_emoji_count  comment_emoji_count_distinct  comment_time_difference  \
0                    2                             2                       95   

   comment_likes  post_count  video_count  highlight_reel_count  \
0            967        76.0          6.0                   8.0   

   hide_like_and_view_counts  has_guides  has_clips  is_private  \
0                        0.0         0.0        1.0         0.0   

   is_embeds_disabled  is_joined_recently  is_professional_account  \
0                 0.0                 0.0                      0.0   

   is_business_account business_contact_method business_category_name  \
0                  0.0                 UNKNOWN                   None   

  category_name category_enum  should_show_category  \
0          None          None                   0.0   

   should_show_public_contacts  \
0                          0.0   

                                  posts_concat_likes  \
0  201,143,127,253,196,356,90,298,247,223,91,78,1...   

             posts_concat_is_video  \
0  1,1,1,0,0,0,1,0,0,1,1,1,0,1,0,1   

                            posts_concat_video_views  \
0  5919,822,1509,0,0,0,1728,0,0,3396,1397,2206,0,...   

                               posts_concat_comments  \
0  6.0,39.0,27.0,19.0,3.0,94.0,13.0,19.0,24.0,9.0...   

                            posts_concat_posted_time  \
0  2021-08-04 17:42:55,2022-10-06 13:37:50,2022-1...   

                                posts_concat_caption  label  \
0  no captionCAPTION_SEPARATORno captionCAPTION_S...      0   

  labelling_technique  binary_label outlier  comment_grams_count  \
0      label_tbl_fake             0                            0   

   comment_length  comment_word_count  
0              29                   7

### 1.2 Comment likes and time difference - 90% done, missing the insights of last chart

There are multiple other columns about the comments of the users. 
* `comment_likes`: the number of likes received by the bots. I suspect them to be inflated by many as found some bots with more than 200 likes seconds after the post was posted. This data is mainly produced by bots (they like themselves and other bots like their comment) but legit users like you and me could also like the comment. 
* `comment_time_difference`: number of seconds between post being publish and the comment of the bots

In [20]:
cols = ['comment_likes', 'comment_time_difference']

print('Missing values: ')
df_main[cols].isna().sum()

Missing values: 


comment_likes              0
comment_time_difference    0
dtype: int64

#### 1.2.1 Comments Likes

In [21]:
df_main.describe_column_by_colcat('comment_likes')[0]

all      0      1    3
count  30420  18553  10928  939
mean     440    611    186   10
std     1624   2054    214   41
min        0      0      0    0
25%       16      6     95    0
50%      112     65    147    0
75%      250    319    239    0
max    77496  77496  13754  245

In [22]:
# Calculating outliers and flagging them
lower, upper = df_main.outliers_bound('comment_likes')
df_main['outlier'] = df_main['comment_likes'].apply(lambda x: '' if lower < x < upper else 'comment_likes')
lower, upper

(0, 601.0)

In [23]:
# Biography length distribution
fig = px.histogram(
    df_main.query('outlier == ""'),
    x='comment_likes', 
    nbins=200,
    color="label",
    opacity=.7,
    marginal="box", # or violin, rug)
    title=f'Distribution of Biography Length per Label for users with biographies',
    **plotly_kwargs
    )

fig = fig.update_layout(barmode='overlay')

# sv.save_plotly_fig(fig)
sv.save_plotly_fig(fig)

In [24]:
(df_main.query('label == 3')['comment_likes'] > 0).value_counts(normalize=True).multiply(100).round(1)

False   90.5
True     9.5
Name: comment_likes, dtype: float64

There's a very clear distinction between the distribution of the likes on the comments. 
* Other bots have almost no likes on their comments. Their Q3 is at 0 and avg at 11 with only 10% of them having at least a like.
* The bots definitely have a weird distribution. It's kinda like waves and they don't have anything between 300 and 500 but then have a bump, this is sus.
* Legit users have what seems to be a very skewed but guessable distribution. The more the likes, the less the people have them.

It'll be interesting to see how that that correlates with time difference

#### 1.2.1 Comment Time Difference

In [25]:
df_main.describe_column_by_colcat('comment_time_difference')[0]

all      0      1      3
count  30420  18553  10928    939
mean    1433   2261     93    652
std     7450   9354   1331   3681
min        4      4      4      6
25%       26     56     18     39
50%       64    145     25     97
75%      232    401     40    300
max    85224  85224  70111  67532

In [26]:
# Calculating outliers and flagging them
lower, upper = df_main.outliers_bound('comment_time_difference')
df_main['outlier'] = df_main['comment_time_difference'].apply(lambda x: '' if lower < x < upper else 'comment_time_difference')
lower, upper

(4, 541.0)

In [27]:
# Biography length distribution
fig = px.histogram(
    df_main.query('outlier == ""'),
    x='comment_time_difference', 
    nbins=200,
    color="label",
    opacity=.7,
    marginal="box", # or violin, rug
    title=f'Distribution of Comment Time Difference per Label<br><sub>Comment time difference is the time difference between the comment and the post in seconds',
    **plotly_kwargs
    )

fig = fig.update_layout(barmode='overlay')
fig  = fig.add_vline(x=0, line_color="green", line_width=2, annotation_text="0")

# sv.save_plotly_fig(fig)
sv.save_plotly_fig(fig)

In [28]:
(df_main.query('label == 3')['comment_likes'] > 0).value_counts(normalize=True).multiply(100).round(1)

False   90.5
True     9.5
Name: comment_likes, dtype: float64

Same as before, there is a clear distinction between the three distribution: 
* Bots are way more skewed towards 0 with most commenting under 70seconds
* legit users 

In [29]:
df_main[[col for col in df_main if 'com' in col and 'post' not in col]].isna().sum()

comment_emoji                   0
comment_emoji_count             0
comment_emoji_count_distinct    0
comment_time_difference         0
comment_likes                   0
comment_grams_count             0
comment_length                  0
comment_word_count              0
dtype: int64

### 1.3 Biography - 90% done


In [30]:
print(f'Nulls: {df_main.biography.isna().sum()}')

Nulls: 0


In [31]:
df_main.biography.describe(include='all')

count     30420
unique    11373
top            
freq       6417
Name: biography, dtype: object

#### 1.3.1 biography wordcloud

In [32]:
# # Plot wordcloud
# for label in (0, 1, 3):
#     print(f'Label: {label}')
#     wordcloud = WordCloud(width=1800, 
#                           height=1200, 
#                           min_font_size=1, 
#                           max_words=500, 
#                           colormap='tab10')
                          
#     word_list = ' '.join([word for list in df_main.query(f'label == {label}')['biography_wo_emoji'].str.split(' ') for word in list])
#     wordcloud.generate(word_list)

#     plt.figure()
#     plt.imshow(wordcloud, interpolation="bilinear")
#     plt.axis("off")
#     plt.savefig(f'{viz_dir}/wordcloud_biography_{label}.png', dpi=300, pad_inches=0.0, bbox_inches='tight')
#     plt.show()

#### 1.3.x bio viz

In [33]:
bots_bios = ' '.join(df_main.query('label == 1')[['username', 'biography_wo_emoji']].drop_duplicates()['biography_wo_emoji'])
bio_words = re.split(' |\n|->|/|-|&', bots_bios)
print(len(bio_words), len(set(bio_words)))

new_df = pd.DataFrame(columns=['word', 'count'])
for word in set(bio_words):
    if word.lower() in stopwords.words('english'): 
        continue

28203 1444


In [34]:
bots_bios = ' '.join(df_main.query('label == 1')[['username', 'biography_wo_emoji']].drop_duplicates()['biography_wo_emoji'])

df_bots_bios = pd.DataFrame(re.split(' |\n|->|/|-|&', bots_bios), columns=['word'])
unique_words = df_bots_bios.drop_duplicates()['word']

new_df = pd.DataFrame(columns=['word', 'count'])
for word in unique_words: 
    if word.lower() in stopwords.words('english'): 
        continue
    try: 
        total = df_main[df_main['biography_wo_emoji'].str.contains(word)]['word'].shape[0]
        new_df.loc[len(new_df)] = [word, total]
    except:
        pass

fig = px.bar(new_df.sort_values('count', ascending=False), x='word', y='count', title='Top 20 words in bot bios')

sv.save_plotly_fig(fig)

/var/folders/p4/gh_zxht10ygcpzccbwwy6rl80000gn/T/ipykernel_18114/1624263468.py:11: UserWarning:

This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.



#### 1.3.2 Calculating bi/tri/quad grams

In [35]:
sub_df = df_main.loc[:, ['biography_wo_emoji', 'label']].drop_duplicates()
df_bio_grams = calculate_grams(sub_df, 'biography_wo_emoji', 20)
df_bio_grams = keep_top_n_grams(df_bio_grams, 30)
sv.save_plotly_fig(plot_grams(df_bio_grams))

#### 1.3.3 Feature engineering
For each biography, count how many of the top30 grams to they have

In [36]:
# Adding tri/quad grams count to main df
bots_triquadgrams = df_bio_grams.query('label > 0 and gram_degree > 2').gram.unique().tolist()

def count_grams(text, grams):
    count = 0
    for gram in grams:
        gram = gram.split(',')
        if all(word in text for word in gram):
            count += 1
    return count


df_main['biography_grams_count'] = df_main.biography_wo_emoji.apply(lambda x: count_grams(x, bots_triquadgrams))

print('% of each label having at least one tri/quad gram')
for label in (0, 1, 3): 
    current_df = df_main.query(f'label == {label}')['biography_grams_count'] > 0
    current_df = current_df.value_counts(normalize=True)
    display(current_df.to_frame(name=f'Label: {label}').round(3))

% of each label having at least one tri/quad gram


Label: 0
False     0.999
True      0.001

Label: 1
False     0.925
True      0.075

Label: 3
False     0.925
True      0.075

In [37]:
# Adding comment length and word count
df_main['biography_length'] = df_main['biography'].str.len()
df_main['biography_word_count'] = df_main['biography'].str.count(' ') + 1
df_main['biography_linebreak_count'] = df_main['biography'].str.count('\n')

# Dropping columns
df_main = df_main.drop(columns=['biography', 'biography_wo_emoji', 'biography_emoji'])
df_main.head(1)

username  biography_emoji_count  \
0  adorable-jade-beluga                    6.0   

   biography_emoji_count_distinct  follow_count  follower_count pronouns  \
0                             6.0       3,164.0         4,676.0     None   

            domain comment_emoji  comment_emoji_count  \
0  mintyswraps.com            👀🏆                    2   

   comment_emoji_count_distinct  comment_time_difference  comment_likes  \
0                             2                       95            967   

   post_count  video_count  highlight_reel_count  hide_like_and_view_counts  \
0        76.0          6.0                   8.0                        0.0   

   has_guides  has_clips  is_private  is_embeds_disabled  is_joined_recently  \
0         0.0        1.0         0.0                 0.0                 0.0   

   is_professional_account  is_business_account business_contact_method  \
0                      0.0                  0.0                 UNKNOWN   

  business_category_name category_name category_enum  should_show_category  \
0                   None          None          None                   0.0   

   should_show_public_contacts  \
0                          0.0   

                                  posts_concat_likes  \
0  201,143,127,253,196,356,90,298,247,223,91,78,1...   

             posts_concat_is_video  \
0  1,1,1,0,0,0,1,0,0,1,1,1,0,1,0,1   

                            posts_concat_video_views  \
0  5919,822,1509,0,0,0,1728,0,0,3396,1397,2206,0,...   

                               posts_concat_comments  \
0  6.0,39.0,27.0,19.0,3.0,94.0,13.0,19.0,24.0,9.0...   

                            posts_concat_posted_time  \
0  2021-08-04 17:42:55,2022-10-06 13:37:50,2022-1...   

                                posts_concat_caption  label  \
0  no captionCAPTION_SEPARATORno captionCAPTION_S...      0   

  labelling_technique  binary_label outlier  comment_grams_count  \
0      label_tbl_fake             0                            0   

   comment_length  comment_word_count  biography_grams_count  \
0              29                   7                      0   

   biography_length  biography_word_count  biography_linebreak_count  
0                73                    13                          3

In [38]:
# Biography length distribution
sub_df = df_main.query('biography_length > 0')
fig = px.histogram(
    sub_df,
    x='biography_length', 
    nbins=50,
    color="label",
    opacity=.7,
    marginal="box", # or violin, rug)
    title=f'Distribution of Biography Length per Label for users with biographies',
    **plotly_kwargs
    )

fig = fig.update_layout(barmode='overlay')

# sv.save_plotly_fig(fig)
sv.save_plotly_fig(fig)

For the users having a biography:
* Legit users tend to have a shorter biography with 50% less than 48 characters. Their IQR is 77 and they occupy all bounds of the distribution. 
* Bots have half of their bio between 55 nd 81 characters (IQR) and generally dont use less than 20 characters or more than 120 
* The other type of bot, also has its own distribution with 75% of their bio having more than 120 characters. 

### 1.4 Follow & Follower Count - Missing insights (markdown)

The columns follow and follower count are the number of people following and being followed by the user.

In [39]:
current_columns = ['follow_count', 'follower_count']
for col in current_columns: 
    print(f'Missing values {col}: {df_main[col].isna().sum()}')

Missing values follow_count: 0
Missing values follower_count: 0


#### 1.4.1 Follow Count

In [40]:
df_describe, fig = df_main.describe_column_by_colcat('follow_count')

display(df_describe)
fig.update_layout(yaxis_range=[0, 2300])
sv.save_plotly_fig(fig)

all      0      1     3
count  30420  18553  10928   939
mean     728    925    300  1811
std     1184   1231    930  1136
min        0      0      0     4
25%       54    232      6  1175
50%      322    536     33  1645
75%      854   1027    228  2207
max     7508   7508   7350  7501

In [41]:
df_main = print_outliers(df_main, 'follow_count')

Lower bound: 0.0 - Upper bound: 2054.0

2533 outliers found

Label: 0


Condition  Count  Percentage
0       True  16625        89.6
1      False   1928        10.4

Label: 1


Condition  Count  Percentage
0       True  10619        97.2
1      False    309         2.8

Label: 3


Condition  Count  Percentage
0       True    643        68.5
1      False    296        31.5

In [42]:
fig = px.histogram(df_main,#.query('outlier.str.contains("follow_count") == False'),
                   x="follow_count", 
                   nbins=500,
                   color="label",
                   opacity=.7,
                   marginal="box", # or violin, rug)
                   title='Distribution of the follow count per label',
                   **plotly_kwargs
                   )


fig = fig.update_layout(barmode='overlay')

# sv.save_plotly_fig(fig)
sv.save_plotly_fig(fig, 'fig')

The distribution of the follow count is very interesting. All labels' interquartile range (between Q1 and Q3) occupy the 0-2.5k follow count range. the main category of bots (sex bots, main obj of the project) tend to follow between 0 and 243 accounts. from 240 to 1,030 there are the legit users and from 1100 to 2.2k, the other type of bot. 


The bots (1) tend to be more about mass commenting, that's how they scam people
The legit user have a larger distribution and are more diverse
The other type of bot have a higher distribution.

#### 1.4.2 Follower count

In [43]:
# Describing column for each label
sub_df, fig = df_main.describe_column_by_colcat('follower_count')

print('Follower count: ')
display(sub_df.style.format('{:,}'))
# sv.save_plotly_fig(fig)

Follower count: 


In [44]:
# Outliers
df_main = print_outliers(df_main, 'follower_count')

Lower bound: 0.0 - Upper bound: 3156.0

4463 outliers found

Label: 0


Condition  Count  Percentage
0       True  14316        77.2
1      False   4237        22.8

Label: 1


Condition  Count  Percentage
0       True  10902        99.8
1      False     26         0.2

Label: 3


Condition  Count  Percentage
0       True    744        79.2
1      False    195        20.8

Seeing the bots at 6k max follower and other bots at 14k, I can assume that none, even if not labelled yet, can have more than 30k followers to be large.

In [45]:
# Plotting follower count distribution
fig = px.histogram(df_main.query('follower_count < 20000'), 
                   x="follower_count", 
                   nbins=200,
                   color="label",
                   opacity=.7,
                   marginal="box", # or violin, rug
                   title='Distribution of the follower count per label.<br><sub>Numbers next to lines are the quantiles.',
                   **plotly_kwargs
                   )

# max_follower_bot = df_main.query('label > 0')['follower_count'].max() * 2

fig = fig.update_layout(barmode='overlay')

sv.save_plotly_fig(fig)

#### 1.3.3 Feature engineering?

### 1.5 Posts, videos and highlight count - Mostly done, missing insights

Those three columns are about the content of the users, counting the posts (photos and videos), videos and highlight reel (old stories showing on profile).

In [46]:
current_columns = ['post_count', 'video_count', 'highlight_reel_count']
for col in current_columns: 
    print(f'Missing values {col}: {df_main[col].isna().sum()}')

Missing values post_count: 0
Missing values video_count: 0
Missing values highlight_reel_count: 0


#### 1.5.1 Post count

In [47]:
# Describing column for each label
sub_df, fig = df_main.describe_column_by_colcat('post_count')

print('Post count described by label: ')
display(sub_df.style.format('{:,}'))
# sv.save_plotly_fig(fig, 'fig')

Post count described by label: 


In [48]:
df_main = print_outliers(df_main, 'post_count')

Lower bound: 0.0 - Upper bound: 78.5

5876 outliers found

Label: 0


Condition  Count  Percentage
0       True  12805        69.0
1      False   5748        31.0

Label: 1


Condition  Count  Percentage
0       True  10806        98.9
1      False    122         1.1

Label: 3


Condition  Count  Percentage
0       True    933        99.4
1      False      6         0.6

Most of the outliers are for the legit users, there's only a small percentage of the bots being outliers compared to the legit users. This is due as the bots need some photos to make people believe they have an account but generally have the same numbers of posts, once they posted their photos they are good. Legit users is the group having the most outliers as people normally have one single acccount where they post photos over the years and more frequently.

In [49]:
# df_main

In [50]:

fig = px.histogram(df_main.query('post_count < 5000'), 
                   x="post_count", 
                   nbins=5000,
                   color="label",
                   opacity=.8,
                   marginal="box", # or violin, rug
                   title='Distribution of the post count per label.',
                   **plotly_kwargs
                   )


fig = fig.update_layout(barmode='overlay', xaxis_range=(0, 100)) # Default range is 0, 100 but can be changed to max by double clicking on plolty viz

sv.save_plotly_fig(fig)

#### 1.5.2 Video Count

In [51]:
# Describing column for each label
sub_df, fig = df_main.describe_column_by_colcat('video_count')

print('Post count described by label: ')
display(sub_df.style.format('{:,}'))
# sv.save_plotly_fig(fig, 'fig')

Post count described by label: 


In [52]:
df_main = print_outliers(df_main, 'video_count')

Lower bound: 0.0 - Upper bound: 0.0

30420 outliers found

Label: 0


Condition  Count  Percentage
0       True  12105        65.2
1      False   6448        34.8

Label: 1


Condition  Count  Percentage
0       True  10625        97.2
1      False    303         2.8

Label: 3


Condition  Count  Percentage
0       True    773        82.3
1      False    166        17.7

In [53]:
fig = px.histogram(df_main.query('video_count < 1000'), 
                   x="video_count", 
                   nbins=1000,
                   color="label",
                   opacity=.8,
                   marginal="box", # or violin, rug
                   title='Distribution of the video count per label (max 1000)',
                   **plotly_kwargs
                   )


fig = fig.update_layout(barmode='overlay', xaxis_range=(0, 100)) # Default range is 0, 100 but can be changed to max by double clicking on plolty viz

sv.save_plotly_fig(fig)

Unsurprisingly, most of the users have 0 video. The legit users have a very skewed distribution with a lot of outliers. 

#### 1.5.3 Highlight Reel Count

In [54]:
# Describing column for each label
sub_df, fig = df_main.describe_column_by_colcat('highlight_reel_count')

print('Post count described by label: ')
display(sub_df.style.format('{:,}'))
sv.save_plotly_fig(fig, 'fig')

Post count described by label: 


In [55]:
df_main = print_outliers(df_main, 'highlight_reel_count')

Lower bound: 0.0 - Upper bound: 5.0

4882 outliers found

Label: 0


Condition  Count  Percentage
0       True  15135        81.6
1      False   3418        18.4

Label: 1


Condition  Count  Percentage
0       True  10817        99.0
1      False    111         1.0

Label: 3


Condition  Count  Percentage
0      False    570        60.7
1       True    369        39.3

In [56]:

fig = px.histogram(df_main.query('highlight_reel_count < 1000'), 
                   x="highlight_reel_count", 
                   nbins=1000,
                   color="label",
                   opacity=.8,
                   marginal="box", # or violin, rug
                   title='Distribution of the highlight reel count per label',
                   **plotly_kwargs
                   )


fig = fig.update_layout(barmode='overlay', xaxis_range=(0, 100)) # Default range is 0, 100 but can be changed to max by double clicking on plolty viz

sv.save_plotly_fig(fig, 'fig')

In [57]:
for i in range(5): 
    p = df_main.query(f'highlight_reel_count >= {i} and label == 3').shape[0] / df_main.query(f'label == 3').shape[0]
    print(f'{p:.0%} of the bots have {i} or more highlight reels')

100% of the bots have 0 or more highlight reels
80% of the bots have 1 or more highlight reels
76% of the bots have 2 or more highlight reels
75% of the bots have 3 or more highlight reels
72% of the bots have 4 or more highlight reels


Other tye of bot has its distribution quite different from both other groups. 80% of the other bots have highlight reels, quite an important feature for them.

### 1.6 Pronouns - Done ✅

In [58]:
# Checking for missing values
for label in (0, 1, 3): 
    sub_df = df_main.query(f"label == {label}")
    p = sub_df['pronouns'].isna().sum() / sub_df.shape[0] * 100
    print(f'Label: {label} - % of users with pronouns: {p:.2f}%')

Label: 0 - % of users with pronouns: 96.82%
Label: 1 - % of users with pronouns: 99.94%
Label: 3 - % of users with pronouns: 99.68%


Most of the users having a pronoun are legit users and but some bots have it too. There are a ton of missing values (>98%) so I'll just create a flag for originally missing/not missing.

In [59]:
df_main['pronouns_na_flag'] = df_main['pronouns'].isna().astype(int)
df_main = df_main.drop('pronouns', axis=1)
df_main.head(1)

username  biography_emoji_count  \
0  adorable-jade-beluga                    6.0   

   biography_emoji_count_distinct  follow_count  follower_count  \
0                             6.0       3,164.0         4,676.0   

            domain comment_emoji  comment_emoji_count  \
0  mintyswraps.com            👀🏆                    2   

   comment_emoji_count_distinct  comment_time_difference  comment_likes  \
0                             2                       95            967   

   post_count  video_count  highlight_reel_count  hide_like_and_view_counts  \
0        76.0          6.0                   8.0                        0.0   

   has_guides  has_clips  is_private  is_embeds_disabled  is_joined_recently  \
0         0.0        1.0         0.0                 0.0                 0.0   

   is_professional_account  is_business_account business_contact_method  \
0                      0.0                  0.0                 UNKNOWN   

  business_category_name category_name category_enum  should_show_category  \
0                   None          None          None                   0.0   

   should_show_public_contacts  \
0                          0.0   

                                  posts_concat_likes  \
0  201,143,127,253,196,356,90,298,247,223,91,78,1...   

             posts_concat_is_video  \
0  1,1,1,0,0,0,1,0,0,1,1,1,0,1,0,1   

                            posts_concat_video_views  \
0  5919,822,1509,0,0,0,1728,0,0,3396,1397,2206,0,...   

                               posts_concat_comments  \
0  6.0,39.0,27.0,19.0,3.0,94.0,13.0,19.0,24.0,9.0...   

                            posts_concat_posted_time  \
0  2021-08-04 17:42:55,2022-10-06 13:37:50,2022-1...   

                                posts_concat_caption  label  \
0  no captionCAPTION_SEPARATORno captionCAPTION_S...      0   

  labelling_technique  binary_label  \
0      label_tbl_fake             0   

                                             outlier  comment_grams_count  \
0  , follow_count, follower_count, video_count, h...                    0   

   comment_length  comment_word_count  biography_grams_count  \
0              29                   7                      0   

   biography_length  biography_word_count  biography_linebreak_count  \
0                73                    13                          3   

   pronouns_na_flag  
0                 1

### 1.7 Domain - 70% done

The domain column is the domain url that the users had in their bio bu

#### 1.7.0

In [60]:
na_count = df_main['domain'].isna().sum()
print(f"The domain column has {na_count:,} ({na_count / df_main.shape[0]:.1%}) missing values (no link in bio).")

The domain column has 12,373 (40.7%) missing values (no link in bio).


In [61]:
# sub_df.query('domain_count > 500')

#### 1.7.x adding new columns based on if the website contains words from a list

Blacklist downloaded from: http://dsi.ut-capitole.fr/blacklists/

In [62]:
df_blacklist_domains = df_main[['domain', 'label']].copy(deep=True)
blacklist_domains = {}

# listing all the files as 
for root, dirs, files in os.walk('data/blacklists_domains'):
    for filename in files:
        file_path = os.path.join(root, filename)
        
        if file_path[-7:] == 'domains': 
            category = file_path.split('/')[-2]
            with open(file_path, 'r') as f:
                blacklist_domains.update({category: f.read().splitlines()})

blacklist_domains.update({'None': [None]})

domain_category_to_keep = ('None', 'shortener', 'audio-video', 'social_networks', 'associations_religieuses', 'sports', 'shopping', 'bitcoin', 'webmail', 'cryptojacking', 'press', 'adult', 'malware', 'phishing')
for category, domains in tqdm(blacklist_domains.items()): 
    if category in domain_category_to_keep:
        if category in ('bitcoin', 'cryptojacking'):
            category = 'crypto'
        
        df_blacklist_domains[category] = df_blacklist_domains['domain'].parallel_apply(lambda x: 1 if x in domains else 0)

100%|██████████| 1/1 [00:00<00:00,  7.38it/s]


In [63]:
df_blacklist_domains.sum(axis=0, numeric_only=True).sort_values(ascending=False).head(20)

label    13745
None     12373
dtype: int64

In [64]:
df_blacklist_domains.melt(['domain']).query('domain == "linktr.ee" and value > 0').drop_duplicates()

domain variable  value
48    linktr.ee    label      1
1147  linktr.ee    label      3

In [65]:
df_blacklist_domains.melt(['domain', 'label'])[['domain', 'variable', 'value']].query('value > 0').drop_duplicates().groupby('domain', as_index=False).count().sort_values('variable', ascending=False).head(20)

Empty DataFrame
Columns: [domain, variable, value]
Index: []

In [66]:
df_double = pd.concat([df_main['domain'], df_blacklist_domains.sum(axis=1)], axis=1).rename({0: 'blacklist_count'}, axis=1).sort_values('blacklist_count', ascending=False).drop_duplicates().head(20)
df_double


# px.sunburst(df_double, path=['domain', 'blacklist_count'], values='blacklist_count', title='Top 20 domains with the most blacklists')

/var/folders/p4/gh_zxht10ygcpzccbwwy6rl80000gn/T/ipykernel_18114/2652266599.py:1: FutureWarning:

Dropping of nuisance columns in DataFrame reductions (with 'numeric_only=None') is deprecated; in a future version this will raise TypeError.  Select only valid columns before calling the reduction.



domain  blacklist_count
14889                              None                4
18526                          sfox.com                3
10035                             wa.me                3
15776                      coin-nex.com                3
3229                          linkr.bio                3
4653                        bitcoin.com                3
4207                       coinmama.com                3
21080                         linktr.ee                3
5191                        pipcount.uk                3
23531                  pipcountfx.co.uk                3
18528                      coinbase.com                3
5197   cryptomaxprofit.godaddysites.com                3
13116                       moonpay.com                3
19896           cryptotradefxdirect.com                3
5187                      fxoptions.com                3
5192               cryptostockminer.com                3
13087                       coin360.com                3
10032             cryptolivetrading.ltd                3
29753                        crypto.com                3
16074             springcryptotrade.com                3

In [67]:
sub_df = df_blacklist_domains.melt(id_vars=['domain', 'label'])[['domain', 'variable']].drop_duplicates()

sub_df.groupby(['variable', 'domain'], as_index=False)#.rename({'domain': 'count'}, axis=1).sort_values('count', ascending=False)

In [68]:
cols = df_blacklist_domains.sum()[df_blacklist_domains.sum().gt(0)].index
df_blacklist_domains.query('domain == "twitch.com"')[[col for col in cols if df_blacklist_domains[col].sum() > 0]]

/var/folders/p4/gh_zxht10ygcpzccbwwy6rl80000gn/T/ipykernel_18114/1863344820.py:1: FutureWarning:

The default value of numeric_only in DataFrame.sum is deprecated. In a future version, it will default to False. In addition, specifying 'numeric_only=None' is deprecated. Select only valid columns or specify the value of numeric_only to silence this warning.

/var/folders/p4/gh_zxht10ygcpzccbwwy6rl80000gn/T/ipykernel_18114/1863344820.py:1: FutureWarning:

The default value of numeric_only in DataFrame.sum is deprecated. In a future version, it will default to False. In addition, specifying 'numeric_only=None' is deprecated. Select only valid columns or specify the value of numeric_only to silence this warning.



label  None
22052      0     0

In [69]:
df_blacklist_domains = pd.concat([df_blacklist_domains[[col for col in df_blacklist_domains if col != 'label']], df_main['label']], axis=1)
df_blacklist_domains.melt(id_vars=['domain', 'label'])
# df_blacklist_domains

domain  label variable  value
0      mintyswraps.com      0     None      0
1          youtube.com      0     None      0
2                 None      0     None      1
3                 None      0     None      1
4                 None      0     None      1
...                ...    ...      ...    ...
30415     fanofno1.com      0     None      0
30416             None      0     None      1
30417        linkr.bio      1     None      0
30418        linkr.bio      1     None      0
30419          solo.to      0     None      0

[30420 rows x 4 columns]

#### 1.7.x viz

In [70]:
sub_df = df_blacklist_domains.melt(id_vars=['domain', 'label']).query('value > 0')


data = sub_df['variable'].value_counts(normalize=True).multiply(100).round(2).sort_values(ascending=False).head(3).to_dict()
data.update({'other': round(100 - sum(data.values()), 2)})

# fig = go.Figure()
# fig.add_trace(go.Bar(name='All Labels', 
#                         x=list(data.keys()), 
#                         y=list(data.values()), 
#                         text=[str(value) for value in data.values()]))

# fig
data

{'None': 100.0, 'other': 0.0}

In [71]:
sub_df['variable'].value_counts(normalize=True)#.multiply(100).round(2).sort_values(ascending=False)

None   1.0
Name: variable, dtype: float64

In [72]:
df_main['domain_na_flag'] = df_main['domain'].isna().astype(int)

fig = plot_binary_distribution_by_label(df_main, 'domain_na_flag')
sv.save_plotly_fig(fig)

In [73]:
df_blacklist_domains#.melt(id_vars=['domain', 'label'])#.query('value > 0 and variable != "None"')

domain  None  label
0      mintyswraps.com     0      0
1          youtube.com     0      0
2                 None     1      0
3                 None     1      0
4                 None     1      0
...                ...   ...    ...
30415     fanofno1.com     0      0
30416             None     1      0
30417        linkr.bio     0      1
30418        linkr.bio     0      1
30419          solo.to     0      0

[30420 rows x 3 columns]

In [75]:
# sub_df = df_blacklist_domains.melt(id_vars=['domain', 'label']).query('value > 0 and variable != "None"')
# top_n = 45
# labels = sub_df['label'].unique()


# print(len(labels))

# # create a dictionary to map label to subplot index
# label_subplot_dict = {label: i+1 for i, label in enumerate(labels)}

# # create figure with 2 rows and 3 columns (top chart uses 3 columns)
# fig = make_subplots(rows=2, cols=len(labels), 
#                 specs=[[{'rowspan': 1, 'colspan': len(labels)}] + [None, None],
#                     [{'rowspan': 1, 'colspan': 1} for label in labels]],
#                     subplot_titles=['All Labels'] + [f'Label {label}' for label in labels],
#                 y_title='Your master y-title')#, shared_yaxes=True)


# # Adding all data regardless of label
# data = sub_df['variable'].value_counts(normalize=True).multiply(100).round(2).sort_values(ascending=False).head(top_n).to_dict()
# data.update({'other': round(100 - sum(data.values()), 2)})
# fig.add_trace(go.Bar(name='All Labels', 
#                         x=list(data.keys()), 
#                         y=list(data.values()), 
#                         text=[str(value) for value in data.values()]), 
#                 row=1, col=1)


# # subplot_titles=[f'All Labels: n={no:,} / y={yes:,}']
# # label subplots
# for label in sub_df['label'].unique():
#     print(label)
#     data = sub_df.query(f'label == {label}')['variable'].value_counts(normalize=True).multiply(100).round(2).sort_values(ascending=False).head(top_n // 3).to_dict()
#     data.update({'other': round(100 - sum(data.values()), 2)})
#     fig.add_trace(go.Bar(name='All Labels', 
#                             x=list(data.keys()), 
#                             y=list(data.values()), 
#                             text=[str(value) for value in data.values()]), 
                            
#                     row=2, col=label_subplot_dict[label])

# fig.update_layout(height=800, 
#                     title=f'Distribution of Labels by domain category')

# # subplot_titles += [''] + [''] # This is for the x and y main axis titles
# # fig.update_layout(annotations=[{'text': name} for name in subplot_titles])

# sv.save_plotly_fig(fig)

Looking at the domains that the users put on their profile, for the legit users, nothing odd, a variety of users  uses a variety of links from auto-video (spotify, youtube, etc), social medias, games, etc. It's much more different for the bots. The sex bots, for the ones who have a url in their bio, more than 99.5% of them use url shortener like bit.ly, tinyurl, linktr.ee, etc. The other bots have a more diverse domains with mostly shortener and cryptos. 

The sunburst below shows it even better.

In [76]:
sub_df.drop_duplicates()

Empty DataFrame
Columns: [domain, label, variable, value]
Index: []

In [77]:
# d1 = sub_df.query(f'label == {label}').groupby(['domain', 'label', 'variable'], as_index=False).count().sort_values('domain', ascending=False)   
# # d2 = sub_df.query(f'label == {label}').groupby(['variable'], as_index=False).count().sort_values('domain', ascending=False)
# d1.query('label == 1')
# d1[['domain', 'variable', 'value']].values.tolist()

In [78]:
# with open('/Users/marclamy/Desktop/code/viz/instabot/' + 'README.md', 'w') as f:
#     content = f.read()
#     # if viz_path not in f.read():
#     #     f.write(fig_title + '\n' + link + '\n')


# content

In [79]:
# with open('/Users/marclamy/Desktop/code/viz/instabot/README.md', 'w') as f:
#     f.write('### Instabot project\n\n')

In [80]:
# fig_title = 'titlsaasdfddffae'
# html_link = 'link'
# png_link = 'https://github.com/marclelamy/viz/blob/main/instabot/wordcloud_biography_3.png'
# embed = f'![]({png_link})'
# embed += f'[Link for interactibility]({html_link})'

# content = '**' + fig_title + '**\n\n' + embed + '\n\n\n'

# with open('/Users/marclamy/Desktop/code/viz/instabot/README.md', 'r+') as f:
#     if fig_title not in f.read():
#         f.write(content)




# content

In [81]:
fig = make_subplots(rows=1, 
                    cols=3, 
                    specs=[[{'type':'sunburst'}, {'type':'sunburst'}, {'type':'sunburst'}]],
                    subplot_titles=['Label 0', 'Label 1', 'Label 3'])


for index, label in enumerate((0, 1, 3)):
    d1 = sub_df.query(f'label == {label}').groupby(['domain', 'label', 'variable'], as_index=False).count().sort_values('domain', ascending=False)   
    d2 = sub_df.query(f'label == {label}').groupby(['variable'], as_index=False).count().sort_values('domain', ascending=False)


    labels = []
    parents = []
    values = []
    items = d2[['variable', 'domain', 'value']].values.tolist() + d1[['domain', 'variable', 'value']].values.tolist()
    for label, parent, value in items: 
        if '.' not in label: 
            parent = ''
        labels.append(label)
        parents.append(parent)
        values.append(value)

    fig.add_trace(
        go.Sunburst(
            labels=labels,
            parents=parents,
            values=values,
            branchvalues="total",

            ), row=1, col=index+1)


fig.update_layout(title=f'Sunburst of domains by label for domains and their category')


sv.save_plotly_fig(fig)

#### 1.7.x Feature Engineering

In [82]:
# Adding columns to df main
df_blacklist_domains = df_blacklist_domains.drop(['label', 'domain'], axis=1)
df_blacklist_domains.columns = [f'domain_{col}' for col in df_blacklist_domains.columns]
df_main = pd.concat([df_main, df_blacklist_domains], axis=1).drop(['domain'], axis=1)
df_main

username  biography_emoji_count  \
0                adorable-jade-beluga                    6.0   
1           hysterical-glistening-bee                    2.0   
2                  little-crafty-mink                    0.0   
3                 gentle-crimson-wolf                    1.0   
4                festive-uppish-leech                    0.0   
...                               ...                    ...   
30415      attentive-mongoose-of-hail                    1.0   
30416    resourceful-thistle-toucanet                    3.0   
30417           glorious-zippy-agouti                    9.0   
30418  hopping-stallion-of-conversion                    3.0   
30419            loud-nondescript-elk                    2.0   

       biography_emoji_count_distinct  follow_count  follower_count  \
0                                 6.0       3,164.0         4,676.0   
1                                 2.0         114.0            52.0   
2                                 0.0         204.0           422.0   
3                                 1.0         211.0           586.0   
4                                 0.0           0.0             0.0   
...                               ...           ...             ...   
30415                             1.0         278.0           330.0   
30416                             3.0       1,251.0           373.0   
30417                             8.0           0.0           253.0   
30418                             2.0           7.0           918.0   
30419                             1.0       2,733.0        15,392.0   

      comment_emoji  comment_emoji_count  comment_emoji_count_distinct  \
0                👀🏆                    2                             2   
1                🤣😭                    3                             2   
2                 😂                    1                             1   
3                 😂                    1                             1   
4                 🤪                    2                             1   
...             ...                  ...                           ...   
30415                                  0                             0   
30416             🥱                    1                             1   
30417             💫                    1                             1   
30418             🐮                    1                             1   
30419                                  0                             0   

       comment_time_difference  comment_likes  post_count  video_count  \
0                           95            967        76.0          6.0   
1                          250           1024         0.0          2.0   
2                          310            711         0.0          0.0   
3                          180            161         6.0          0.0   
4                          245            166         0.0          0.0   
...                        ...            ...         ...          ...   
30415                      211            165         2.0          0.0   
30416                       30              4        22.0          1.0   
30417                       12            134         9.0          0.0   
30418                       62             70         6.0          0.0   
30419                      428            714     2,594.0         20.0   

       highlight_reel_count  hide_like_and_view_counts  has_guides  has_clips  \
0                       8.0                        0.0         0.0        1.0   
1                       0.0                        0.0         0.0        1.0   
2                       0.0                        1.0         0.0        0.0   
3                       0.0                        0.0         0.0        0.0   
4                       0.0                        0.0         0.0        0.0   
...                     ...                        ...         ...        ...   
30415                   0.0                        0.0        

### 1.8 Professional/business columns - Done ✅

There are multiple columns like: `is_business_account`, `is_professional_account`, `category_enum`, `category_name`, `business_category_name`, `business_contact_method`

In [83]:
business_columns = ['is_business_account', 'is_professional_account', 'category_enum', 'category_name', 'business_category_name', 'business_contact_method']

sub_df = df_main[business_columns + ['label']]

for col in business_columns: 
    col_na = sub_df[col].isna()
    if col_na.sum() != 0:
        sub_df[col] = sub_df[col].isna().astype(int)

sub_df.groupby(business_columns, as_index=False)['label'].count()

/var/folders/p4/gh_zxht10ygcpzccbwwy6rl80000gn/T/ipykernel_18114/1305034588.py:8: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



is_business_account  is_professional_account  category_enum  \
0                   0.0                      0.0              1   
1                   0.0                      0.0              1   
2                   0.0                      1.0              1   
3                   0.0                      1.0              1   
4                   0.0                      1.0              1   
5                   1.0                      1.0              0   
6                   1.0                      1.0              0   
7                   1.0                      1.0              0   
8                   1.0                      1.0              0   
9                   1.0                      1.0              0   
10                  1.0                      1.0              0   
11                  1.0                      1.0              1   
12                  1.0                      1.0              1   
13                  1.0                      1.0              1   
14                  1.0                      1.0              1   
15                  1.0                      1.0              1   
16                  1.0                      1.0              1   

    category_name  business_category_name  business_contact_method  label  
0               1                       1                        0   1326  
1               1                       1                        1  20364  
2               0                       1                        0    782  
3               0                       1                        1   4990  
4               1                       1                        1      3  
5               0                       0                        0    719  
6               0                       0                        1   1545  
7               0                       1                        0      6  
8               0                       1                        1      5  
9               1                       0                        0     35  
10              1                       0                        1     49  
11              0                       0                        0     80  
12              0                       0                        1    462  
13              1                       0                        0      7  
14              1                       0                        1     38  
15              1                       1                        0      8  
16              1                       1                        1      1

### check shit here

In [84]:
# df_business_groupby = df_main.groupby(['is_professional_account', 'is_business_account', 'label'], as_index=False)['username'].count()
# df_business_groupby['count_%'] = df_business_groupby['username'] / df_business_groupby['username'].sum()
# import matplotlib.cm
# # display(df_business_groupby.style.background_gradient())
# # df_business_groupby

Many bots are creating professional or business accounts. Seems like if you're a business, you're a professional but if you're pro, you're not necessarily a business. The highest combination is that most legit users and bots don't have a professional account. It's good to note that for the otherbots, there are as more accounts as professionals/business than normal accounts.

In [85]:
px.sunburst(df_main.dropna(subset='category_enum').fillna('na'),
            path=['category_enum', 'category_name'],
            color='label',
            ).update_layout(uniformtext=dict(minsize=10, mode='hide'))

In [86]:
# asdf

In [87]:
fig = px.histogram(df_main, 
                    x='category_name', 
                    color='label',
                    title=f'Distribution of labels for each category of category_name for bots and legit users')

fig = fig.update_xaxes(tickangle=-90, categoryorder='total descending') 
sv.save_plotly_fig(fig)

In [88]:
fig = px.histogram(df_main.query('label > 0'), 
                    x='category_name', 
                    color='label',
                    title=f'Distribution of labels for each category of category_name for bots only')

fig = fig.update_xaxes(tickangle=-90, categoryorder='total descending') 
sv.save_plotly_fig(fig)

In [89]:
fig = px.histogram(df_main.query('label > 0'), 
                    x='business_category_name', 
                    color='label',
                    title=f'Distribution of labels for each category of business_category_name for bots and legit users')

fig = fig.update_xaxes(tickangle=-90, categoryorder='total descending') 
sv.save_plotly_fig(fig) 

It's interesting to see the difference between the bots and the sex bots. Even though many have been miss labelled (they'll both be marked at 1 when developping the model) bet ween bot or otherbot, there is a significative distinction between how they identify themselves.

Other bots seems to be more entreupreuners, financial service or investment firm where bots are more video creator (you bet), personnal blog or gamer.

In [90]:
df_main.query('label > 0')['category_name'].value_counts().sort_values(ascending=True)[df_main.query('label > 0')['category_name'].value_counts().sort_values(ascending=True).lt(12)].index

Index(['Real Estate', 'Video Game Store', 'Drive In Restaurant', 'Cars',
       'Coach', 'Trade School', 'Computer Training School', 'Sports',
       'Education', 'Just for fun', 'Legal', 'Dancer',
       'Music Production Studio', 'Franchise Broker', 'Entertainment website',
       'Beauty, cosmetic & personal care', 'Marketing Agency', 'Writer',
       'Health/beauty', 'Author', 'Scientist', 'Preschool', 'Athlete',
       'Financial Consultant', 'Insurance Broker', 'Dessert Shop',
       'Drug Addiction Treatment Center', 'Music video', 'Shopping & retail',
       'Photographer', 'Musician', 'Local business', 'Clothing (Brand)',
       'Digital creator', 'Public figure', 'Art', 'Musician/band', 'Blogger'],
      dtype='object')

In [91]:
# Keeping only binary columns
df_main = df_main.drop(['category_name', 'business_category_name', 'business_contact_method', 'category_enum', 'should_show_category'], axis=1)

In [92]:
df_main

username  biography_emoji_count  \
0                adorable-jade-beluga                    6.0   
1           hysterical-glistening-bee                    2.0   
2                  little-crafty-mink                    0.0   
3                 gentle-crimson-wolf                    1.0   
4                festive-uppish-leech                    0.0   
...                               ...                    ...   
30415      attentive-mongoose-of-hail                    1.0   
30416    resourceful-thistle-toucanet                    3.0   
30417           glorious-zippy-agouti                    9.0   
30418  hopping-stallion-of-conversion                    3.0   
30419            loud-nondescript-elk                    2.0   

       biography_emoji_count_distinct  follow_count  follower_count  \
0                                 6.0       3,164.0         4,676.0   
1                                 2.0         114.0            52.0   
2                                 0.0         204.0           422.0   
3                                 1.0         211.0           586.0   
4                                 0.0           0.0             0.0   
...                               ...           ...             ...   
30415                             1.0         278.0           330.0   
30416                             3.0       1,251.0           373.0   
30417                             8.0           0.0           253.0   
30418                             2.0           7.0           918.0   
30419                             1.0       2,733.0        15,392.0   

      comment_emoji  comment_emoji_count  comment_emoji_count_distinct  \
0                👀🏆                    2                             2   
1                🤣😭                    3                             2   
2                 😂                    1                             1   
3                 😂                    1                             1   
4                 🤪                    2                             1   
...             ...                  ...                           ...   
30415                                  0                             0   
30416             🥱                    1                             1   
30417             💫                    1                             1   
30418             🐮                    1                             1   
30419                                  0                             0   

       comment_time_difference  comment_likes  post_count  video_count  \
0                           95            967        76.0          6.0   
1                          250           1024         0.0          2.0   
2                          310            711         0.0          0.0   
3                          180            161         6.0          0.0   
4                          245            166         0.0          0.0   
...                        ...            ...         ...          ...   
30415                      211            165         2.0          0.0   
30416                       30              4        22.0          1.0   
30417                       12            134         9.0          0.0   
30418                       62             70         6.0          0.0   
30419                      428            714     2,594.0         20.0   

       highlight_reel_count  hide_like_and_view_counts  has_guides  has_clips  \
0                       8.0                        0.0         0.0        1.0   
1                       0.0                        0.0         0.0        1.0   
2                       0.0                        1.0         0.0        0.0   
3                       0.0                        0.0         0.0        0.0   
4                       0.0                        0.0         0.0        0.0   
...                     ...                        ...         ...        ...   
30415                   0.0                        0.0        

---

In [93]:
df_main.head()

username  biography_emoji_count  \
0       adorable-jade-beluga                    6.0   
1  hysterical-glistening-bee                    2.0   
2         little-crafty-mink                    0.0   
3        gentle-crimson-wolf                    1.0   
4       festive-uppish-leech                    0.0   

   biography_emoji_count_distinct  follow_count  follower_count comment_emoji  \
0                             6.0       3,164.0         4,676.0            👀🏆   
1                             2.0         114.0            52.0            🤣😭   
2                             0.0         204.0           422.0             😂   
3                             1.0         211.0           586.0             😂   
4                             0.0           0.0             0.0             🤪   

   comment_emoji_count  comment_emoji_count_distinct  comment_time_difference  \
0                    2                             2                       95   
1                    3                             2                      250   
2                    1                             1                      310   
3                    1                             1                      180   
4                    2                             1                      245   

   comment_likes  post_count  video_count  highlight_reel_count  \
0            967        76.0          6.0                   8.0   
1           1024         0.0          2.0                   0.0   
2            711         0.0          0.0                   0.0   
3            161         6.0          0.0                   0.0   
4            166         0.0          0.0                   0.0   

   hide_like_and_view_counts  has_guides  has_clips  is_private  \
0                        0.0         0.0        1.0         0.0   
1                        0.0         0.0        1.0         0.0   
2                        1.0         0.0        0.0         1.0   
3                        0.0         0.0        0.0         0.0   
4                        0.0         0.0        0.0         1.0   

   is_embeds_disabled  is_joined_recently  is_professional_account  \
0                 0.0                 0.0                      0.0   
1                 0.0                 0.0                      1.0   
2                 0.0                 0.0                      0.0   
3                 0.0                 0.0                      0.0   
4                 0.0                 0.0                      0.0   

   is_business_account  should_show_public_contacts  \
0                  0.0                          0.0   
1                  0.0                          1.0   
2                  0.0                          0.0   
3                  0.0                          0.0   
4                  0.0                          0.0   

                                  posts_concat_likes  \
0  201,143,127,253,196,356,90,298,247,223,91,78,1...   
1                                               None   
2                                               None   
3                            246,231,202,193,128,127   
4                                               None   

             posts_concat_is_video  \
0  1,1,1,0,0,0,1,0,0,1,1,1,0,1,0,1   
1                             None   
2                             None   
3                      0,0,0,0,0,0   
4                             None   

                            posts_concat_video_views  \
0  5919,822,1509,0,0,0,1728,0,0,3396,1397,2206,0,...   
1                                               None   
2                                               None   
3                                        0,0,0,0,0,0   
4                                               None   

                               posts_concat_comments  \
0  6.0,39.0,27.0,19.0,3.0,94.0,13.0,19.0,24.0,9.0...   
1                                               None   
2                                               None   
3                            2

### 1.9 Binary columns

Here, I'm gonna treat all the binary columns, the one with True/False. Those columns are: 
* has_guides: 
* has_clips
* is_private: The user has a private account (only followers can see their posts)
* is_embeds_disabled: whether the post or media item can be embedded on another website or platform.
* is_joined_recently: whether the user has joined Instagram recently	
* should_show_public_contacts: 

#### 1.9.1 has_guides

whether an Instagram profile has any Guides associated with it or not. Guides are a feature on Instagram that allow users to create and share curated collections of posts and other content, with the goal of providing a more immersive and informative experience around a particular topic.

In [94]:
fig = plot_binary_distribution_by_label(df_main, 'has_guides')
sv.save_plotly_fig(fig)

Almost all of the users don't have any guides. The only legit users have guides but only 1.1% of them which is very low.The column is likely to be very weak predictor, but I'll keep it for now.

#### 1.9.2 has_clips

In [95]:
fig = plot_binary_distribution_by_label(df_main, 'has_clips')
sv.save_plotly_fig(fig)

In here, the data is highly skewed, most of the users don't have any clips but then ones who have the most are the legit users where 26% of them have some. Both other bots have a very low percentage of users having clips.

#### 1.9.3 is_private

In [96]:
fig = plot_binary_distribution_by_label(df_main, 'is_private')
sv.save_plotly_fig(fig)

Once again, skewed data. Legit users and classic bots have a similar percentage of private accounts, about 25-30% versus a percent for the other bots.

When scraping and looking at the user during the whole project, I found many bots that were private. I wonder what the real reason is 

#### 1.9.4 is_embeds_disabled

In [97]:
fig = plot_binary_distribution_by_label(df_main, 'is_embeds_disabled')
sv.save_plotly_fig(fig)

This is the most skewed feature of the binary ones, most of the users have embeds enabled. Only a very few users have it disable for some reason.

#### 1.9.5 is_joined_recently

In [98]:
fig = plot_binary_distribution_by_label(df_main, 'is_joined_recently')
sv.save_plotly_fig(fig)

This is the most skewed feature of the binary ones, most of the users have embeds enabled. Only a very few users have it disable for some reason.

#### 1.9.6 should_show_public_contacts

In [99]:
fig = plot_binary_distribution_by_label(df_main, 'should_show_public_contacts')
sv.save_plotly_fig(fig)

##### 1.9.7 is_verified

In [100]:
# fig = plot_binary_distribution_by_label(df_main, 'is_verified')
# sv.save_plotly_fig

In [101]:
# Dropping is_verified as it's a constant value
# df_main = df_main.drop('is_verified', axis=1)

### 1.10 Users' posts list

When collecting users' profile data, Instagram returns by default the last 12 posts of the users. Each posts have multiple attributes like the number of likes, comments, when the post was posted, etc. I'm gonna explore those and see what can I get from them. 

The data is not in a format usable so I'll have to summarize each of the different lists. The process: 
* Count how many posts I have the data on. Some users are private which prevents me from knowing anything about their posts
* Aggregate all the lists to extract new features: 
    * For columns as likes, video_view, comments, I can get the total, mean and median. 
    * For columns as posted time, I can get the difference between first and last posts and average diff between each posts
    * For the caption, I can extract if the user tagged anyone or....???


Im not suer who generated the data for those columns. For the likes on the comments, I knew for a fact that many bots like other's comments. I don't know if that's the case for the likes and comment received by the users on their posts. I'll keep all the columns regardless and see what I can do with them.

In [102]:
# query = '''  
# SELECT 
#     * 
    
# FROM new_clean_comments_users_last12_test
# where 1=1
#     and posts_concat_posted_time is not null
# '''

# df_posts = pd.read_sql_query(query, con)
# df_posts = df_posts[[col for col in df_posts if 'posts_concat' in col or col in ['username', 'label']]].drop_duplicates().dropna()
# df_posts

# sadfg

In [210]:
df_main = get_main()
df_posts = df_main[[col for col in df_main if 'posts_concat' in col or col in ['username', 'label', 'binary_label', 'post_count', 'is_private']]].drop_duplicates().dropna()

# Changing the values of the columns to lists
post_cols = ['posts_concat_likes',	'posts_concat_is_video', 'posts_concat_video_views', 'posts_concat_comments', 'posts_concat_posted_time']
for col in post_cols: 
    df_posts[col] = df_posts[col].apply(lambda x: x.split(',') if pd.notna(x) else x)
df_posts['posts_concat_caption'] = df_posts['posts_concat_caption'].apply(lambda x: x.split('CAPTION_SEPARATOR') if pd.notna(x) else x)

df_posts['posts_fetch_count'] = df_posts['posts_concat_likes'].apply(lambda x: len(x) if isinstance(x, list) else x)
# df_posts = df_posts.explode(post_cols + ['posts_concat_caption'])
df_posts

username  post_count  is_private  \
0                adorable-jade-beluga        76.0         0.0   
3                 gentle-crimson-wolf         6.0         0.0   
8       calculating-tiger-of-security        63.0         0.0   
9          gorgeous-nimble-sidewinder       334.0         0.0   
10             hopeful-flashy-giraffe       258.0         0.0   
...                               ...         ...         ...   
30405      attractive-naughty-boobook       159.0         0.0   
30407   crouching-phenomenal-toucanet         3.0         0.0   
30408  petite-tarantula-of-completion         1.0         0.0   
30413          perky-curious-elephant        44.0         0.0   
30419            loud-nondescript-elk     2,594.0         0.0   

                                      posts_concat_likes  \
0      [201, 143, 127, 253, 196, 356, 90, 298, 247, 2...   
3                         [246, 231, 202, 193, 128, 127]   
8      [32, 118, 136, 127, 98, 70, 69, 49, 35, 29, 14...   
9          [22, 3, 3, 15, 10, 14, 20, 17, 10, 7, 36, 11]   
10     [466, 498, 409, 640, 684, 687, 676, 1543, 642,...   
...                                                  ...   
30405  [333, 155, 740, 286, 389, 469, 120, 348, 1690,...   
30407                                       [49, 38, 34]   
30408                                              [228]   
30413   [56, 40, 56, 57, 60, 56, 55, 31, 63, 63, 81, 51]   
30419   [8, 36, 67, 9, 136, 50, 22, 23, 826, 36, 24, 24]   

                                  posts_concat_is_video  \
0      [1, 1, 1, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 1, 0, 1]   
3                                    [0, 0, 0, 0, 0, 0]   
8                  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
9                  [0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0]   
10                 [0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1]   
...                                                 ...   
30405  [0, 0, 0, 0, 1, 1, 0, 0, 0, 1, 1, 1, 0, 0, 0, 0]   
30407                                         [0, 0, 0]   
30408                                               [0]   
30413              [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
30419              [0, 0, 1, 0, 1, 0, 0, 0, 1, 0, 0, 0]   

                                posts_concat_video_views  \
0      [5919, 822, 1509, 0, 0, 0, 1728, 0, 0, 3396, 1...   
3                                     [0, 0, 0, 0, 0, 0]   
8                   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
9                 [0, 36, 0, 0, 0, 42, 0, 0, 0, 0, 0, 0]   
10            [0, 0, 0, 0, 0, 0, 0, 9162, 0, 0, 0, 3449]   
...                                                  ...   
30405  [0, 0, 0, 0, 2530, 2802, 0, 0, 0, 4452, 1347, ...   
30407                                          [0, 0, 0]   
30408                                                [0]   
30413               [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
30419       [0, 0, 567, 0, 2196, 0, 0, 0, 2005, 0, 0, 0]   

                                   posts_concat_comments  \
0      [6.0, 39.0, 27.0, 19.0, 3.0, 94.0, 13.0, 19.0,...   
3                         [2.0, 2.0, 2.0, 6.0, 1.0, 2.0]   
8      [4.0, 17.0, 31.0, 9.0, 7.0, 6.0, 4.0, 2.0, 0.0...   
9      [5.0, 1.0, 0.0, 0.0, 2.0, 1.0, 1.0, 0.0, 5.0, ...   
10     [80.0, 77.0, 32.0, 95.0, 58.0, 72.0, 66.0, 29....   
...                                                  ...   
30405  [13.0, 15.0, 43.0, 17.0, 37.0, 40.0, 1.0, 14.0...   
30407                                    [0.0, 1.0, 1.0]   
30408                                             [37.0]   
30413  [1.0, 3.0, 3.0, 6.0, 2.0, 3.0, 1.0, 6.0, 0.0, ...   
30419  [0.0, 1.0, 2.0, 2.0, 4.0, 11.0, 5.0, 1.0, 5.0,...   

                                posts_concat_posted_time  \
0      [2021-08-04 17:42:55, 2022-10-06 13:37:50, 202...   
3      [2020-05-29 15:10:42, 2020-04-11 19:04:58, 202...   
8      [2021-12-09 17:34:14, 2020-12-21 11:18:16, 201...   
9      [2022-01-17 23:52:09, 2022-01-13 04:17:57, 202...   
10     [2022-01-18 16:43:05, 2022-01-18 06:40:15, 202...   
...             

#### 1.10.1 Counting the number of posts & Sum, med, mean

In [211]:
# def aggregate_posts_col(df, col, agg_func):
#     df = df.explode(col)
#     df = df.groupby('username').agg({col: agg_func}).reset_index().round(2)
#     df.columns = ['_'.join(col).strip() for col in df.columns.values]
#     return df

# df = aggregate_posts_col(df_posts[['username', 'posts_concat_likes']], 'posts_concat_likes', ['median', 'min', 'max'])
# df

#### 1.10.2 Time between posts

When starting the project, I assumed that the profiles of the bots are fast to be created meaning when the guys managing the bots create profiles, they post all photos at the same time with the bio and url. A normal user on the other way, doesn't post a lot of photos at the same time, there are always some days of difference between each posts.

In [212]:
df_posts

username  post_count  is_private  \
0                adorable-jade-beluga        76.0         0.0   
3                 gentle-crimson-wolf         6.0         0.0   
8       calculating-tiger-of-security        63.0         0.0   
9          gorgeous-nimble-sidewinder       334.0         0.0   
10             hopeful-flashy-giraffe       258.0         0.0   
...                               ...         ...         ...   
30405      attractive-naughty-boobook       159.0         0.0   
30407   crouching-phenomenal-toucanet         3.0         0.0   
30408  petite-tarantula-of-completion         1.0         0.0   
30413          perky-curious-elephant        44.0         0.0   
30419            loud-nondescript-elk     2,594.0         0.0   

                                      posts_concat_likes  \
0      [201, 143, 127, 253, 196, 356, 90, 298, 247, 2...   
3                         [246, 231, 202, 193, 128, 127]   
8      [32, 118, 136, 127, 98, 70, 69, 49, 35, 29, 14...   
9          [22, 3, 3, 15, 10, 14, 20, 17, 10, 7, 36, 11]   
10     [466, 498, 409, 640, 684, 687, 676, 1543, 642,...   
...                                                  ...   
30405  [333, 155, 740, 286, 389, 469, 120, 348, 1690,...   
30407                                       [49, 38, 34]   
30408                                              [228]   
30413   [56, 40, 56, 57, 60, 56, 55, 31, 63, 63, 81, 51]   
30419   [8, 36, 67, 9, 136, 50, 22, 23, 826, 36, 24, 24]   

                                  posts_concat_is_video  \
0      [1, 1, 1, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 1, 0, 1]   
3                                    [0, 0, 0, 0, 0, 0]   
8                  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
9                  [0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0]   
10                 [0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1]   
...                                                 ...   
30405  [0, 0, 0, 0, 1, 1, 0, 0, 0, 1, 1, 1, 0, 0, 0, 0]   
30407                                         [0, 0, 0]   
30408                                               [0]   
30413              [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
30419              [0, 0, 1, 0, 1, 0, 0, 0, 1, 0, 0, 0]   

                                posts_concat_video_views  \
0      [5919, 822, 1509, 0, 0, 0, 1728, 0, 0, 3396, 1...   
3                                     [0, 0, 0, 0, 0, 0]   
8                   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
9                 [0, 36, 0, 0, 0, 42, 0, 0, 0, 0, 0, 0]   
10            [0, 0, 0, 0, 0, 0, 0, 9162, 0, 0, 0, 3449]   
...                                                  ...   
30405  [0, 0, 0, 0, 2530, 2802, 0, 0, 0, 4452, 1347, ...   
30407                                          [0, 0, 0]   
30408                                                [0]   
30413               [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
30419       [0, 0, 567, 0, 2196, 0, 0, 0, 2005, 0, 0, 0]   

                                   posts_concat_comments  \
0      [6.0, 39.0, 27.0, 19.0, 3.0, 94.0, 13.0, 19.0,...   
3                         [2.0, 2.0, 2.0, 6.0, 1.0, 2.0]   
8      [4.0, 17.0, 31.0, 9.0, 7.0, 6.0, 4.0, 2.0, 0.0...   
9      [5.0, 1.0, 0.0, 0.0, 2.0, 1.0, 1.0, 0.0, 5.0, ...   
10     [80.0, 77.0, 32.0, 95.0, 58.0, 72.0, 66.0, 29....   
...                                                  ...   
30405  [13.0, 15.0, 43.0, 17.0, 37.0, 40.0, 1.0, 14.0...   
30407                                    [0.0, 1.0, 1.0]   
30408                                             [37.0]   
30413  [1.0, 3.0, 3.0, 6.0, 2.0, 3.0, 1.0, 6.0, 0.0, ...   
30419  [0.0, 1.0, 2.0, 2.0, 4.0, 11.0, 5.0, 1.0, 5.0,...   

                                posts_concat_posted_time  \
0      [2021-08-04 17:42:55, 2022-10-06 13:37:50, 202...   
3      [2020-05-29 15:10:42, 2020-04-11 19:04:58, 202...   
8      [2021-12-09 17:34:14, 2020-12-21 11:18:16, 201...   
9      [2022-01-17 23:52:09, 2022-01-13 04:17:57, 202...   
10     [2022-01-18 16:43:05, 2022-01-18 06:40:15, 202...   
...             

In [213]:
def time_diff_min_max_post (lst): 
    if lst == None:
        return lst
    if len(lst) == 1: 
        return 0
    lst = [datetime.strptime(x, '%Y-%m-%d %H:%M:%S') for x in lst]
    lst.sort(reverse=True)
    return (lst[0] - lst[-1]).total_seconds()


df_posts['time_diff_min_max_post_seconds'] = df_posts['posts_concat_posted_time'].apply(time_diff_min_max_post).astype(int)
df_posts['time_diff_min_max_post_avg'] = (df_posts['time_diff_min_max_post_seconds'] / df_posts['posts_fetch_count']).astype(int)
# df_posts = df_posts.merge(df_posts, on='username', how='left')
df_posts = df_posts.drop('posts_concat_posted_time', axis=1)
df_posts

username  post_count  is_private  \
0                adorable-jade-beluga        76.0         0.0   
3                 gentle-crimson-wolf         6.0         0.0   
8       calculating-tiger-of-security        63.0         0.0   
9          gorgeous-nimble-sidewinder       334.0         0.0   
10             hopeful-flashy-giraffe       258.0         0.0   
...                               ...         ...         ...   
30405      attractive-naughty-boobook       159.0         0.0   
30407   crouching-phenomenal-toucanet         3.0         0.0   
30408  petite-tarantula-of-completion         1.0         0.0   
30413          perky-curious-elephant        44.0         0.0   
30419            loud-nondescript-elk     2,594.0         0.0   

                                      posts_concat_likes  \
0      [201, 143, 127, 253, 196, 356, 90, 298, 247, 2...   
3                         [246, 231, 202, 193, 128, 127]   
8      [32, 118, 136, 127, 98, 70, 69, 49, 35, 29, 14...   
9          [22, 3, 3, 15, 10, 14, 20, 17, 10, 7, 36, 11]   
10     [466, 498, 409, 640, 684, 687, 676, 1543, 642,...   
...                                                  ...   
30405  [333, 155, 740, 286, 389, 469, 120, 348, 1690,...   
30407                                       [49, 38, 34]   
30408                                              [228]   
30413   [56, 40, 56, 57, 60, 56, 55, 31, 63, 63, 81, 51]   
30419   [8, 36, 67, 9, 136, 50, 22, 23, 826, 36, 24, 24]   

                                  posts_concat_is_video  \
0      [1, 1, 1, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 1, 0, 1]   
3                                    [0, 0, 0, 0, 0, 0]   
8                  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
9                  [0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0]   
10                 [0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1]   
...                                                 ...   
30405  [0, 0, 0, 0, 1, 1, 0, 0, 0, 1, 1, 1, 0, 0, 0, 0]   
30407                                         [0, 0, 0]   
30408                                               [0]   
30413              [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
30419              [0, 0, 1, 0, 1, 0, 0, 0, 1, 0, 0, 0]   

                                posts_concat_video_views  \
0      [5919, 822, 1509, 0, 0, 0, 1728, 0, 0, 3396, 1...   
3                                     [0, 0, 0, 0, 0, 0]   
8                   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
9                 [0, 36, 0, 0, 0, 42, 0, 0, 0, 0, 0, 0]   
10            [0, 0, 0, 0, 0, 0, 0, 9162, 0, 0, 0, 3449]   
...                                                  ...   
30405  [0, 0, 0, 0, 2530, 2802, 0, 0, 0, 4452, 1347, ...   
30407                                          [0, 0, 0]   
30408                                                [0]   
30413               [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
30419       [0, 0, 567, 0, 2196, 0, 0, 0, 2005, 0, 0, 0]   

                                   posts_concat_comments  \
0      [6.0, 39.0, 27.0, 19.0, 3.0, 94.0, 13.0, 19.0,...   
3                         [2.0, 2.0, 2.0, 6.0, 1.0, 2.0]   
8      [4.0, 17.0, 31.0, 9.0, 7.0, 6.0, 4.0, 2.0, 0.0...   
9      [5.0, 1.0, 0.0, 0.0, 2.0, 1.0, 1.0, 0.0, 5.0, ...   
10     [80.0, 77.0, 32.0, 95.0, 58.0, 72.0, 66.0, 29....   
...                                                  ...   
30405  [13.0, 15.0, 43.0, 17.0, 37.0, 40.0, 1.0, 14.0...   
30407                                    [0.0, 1.0, 1.0]   
30408                                             [37.0]   
30413  [1.0, 3.0, 3.0, 6.0, 2.0, 3.0, 1.0, 6.0, 0.0, ...   
30419  [0.0, 1.0, 2.0, 2.0, 4.0, 11.0, 5.0, 1.0, 5.0,...   

                                    posts_concat_caption  label  binary_label  \
0      [no caption, no caption, no caption, no captio...      0             0   
3      [Photo by Noah Reed on May 29, 2020. May be an...      0             0   
8      [Photo shared by @bauzb0mb on December 09, 202...      0             0   
9      [Photo shared by B-ILL on January 17, 2022 ta

In [214]:
sub_df, fig = df_posts.describe_column_by_colcat('time_diff_min_max_post_avg')


display(sub_df)
fig

all         0         1         3
count      9033      6548      2017       468
mean    2775962   3739057    104850    812903
std     5637577   6193334   1275781   4715073
min           0         0         0         0
25%          43    176188        14        80
50%      397002   1341114        23     46468
75%     3196387   4840938        28    372187
max    93957355  93957355  34142144  72812236

In [215]:
fig = px.histogram(df_posts, 
                   x="time_diff_min_max_post_avg", 
                   nbins=1000,
                   color="label",
                   opacity=.8,
                   marginal="box", # or violin, rug
                   title='Distribution of the highlight reel count per label',
                   **plotly_kwargs,
                   )


fig = fig.update_layout(barmode='overlay') # Default range is 0, 100 but can be changed to max by double clicking on plolty viz

sv.save_plotly_fig(fig, 'fig')

My assumption that the bot post all their posts at once was correct, 75% of the bots have an average of 13s between each post they posts for the last 12 collected. Once again, there is a distinction between the sex bots and the other bots that have a much higher average time between each post.

This is very significant and will definitely be a helpful feature to differentiate bot from legit users. 

In [216]:
bot95q = df_posts.query('label == 1')['time_diff_min_max_post_avg'].quantile(.95)
print(f'Bot\'s 95th quantile: {round(bot95q)}')

Bot's 95th quantile: 7976


In [217]:
conditions = {f'post_count < 2': [],
              f'post_count >= 2': [],
              f'post_count < 2 and label in (0, 1)': [], 
              f'post_count >= 2 and label in (0, 1)': [], 
              }

threshold = 3600 # 1 hour
col = f'time_diff_min_max_post_avg_ge_{threshold}_flag'
df_posts[col] = (df_posts[f'time_diff_min_max_post_avg'] >= threshold).astype(int)
for condition in conditions.keys():
    sub_df = df_posts.query(condition)[['binary_label', col]].copy()
    corr = sub_df.corr().loc[col, 'binary_label']
    conditions[condition] = round(corr, 2)


print(f'Correlation between {col} and binary_label (1 or 0) for users with\n')
print(tabulate(list(conditions.items()), headers=['Condition', 'Correlation']))

Correlation between time_diff_min_max_post_avg_ge_3600_flag and binary_label (1 or 0) for users with

Condition                              Correlation
-----------------------------------  -------------
post_count < 2                               -0.03
post_count >= 2                              -0.85
post_count < 2 and label in (0, 1)           -0.03
post_count >= 2 and label in (0, 1)          -0.93


It's interesting to see that there is a moderate negative correlation between the time_diff_min_max_post_avg_gt_3600_flag columns and the label for the users with at least 2 posts. The negative correlation is `-0.60` but goes up to `-0.65` when looking at the sex bots only.

In [218]:
df_posts.query('posts_fetch_count > post_count and is_private == False')[['posts_fetch_count', 'post_count', 'username', 'label']]

posts_fetch_count  post_count                           username  label
21                    16        14.0           smooth-anteater-of-chaos      0
86                     7         6.0                 macho-adept-caiman      0
95                     1         0.0        therapeutic-glossy-stallion      0
105                    9         6.0  archetypal-orangutan-of-abundance      0
108                    9         8.0         deft-beagle-of-opportunity      0
...                  ...         ...                                ...    ...
27682                  4         2.0              godlike-zebra-of-fame      0
27792                 17        13.0           loyal-hog-of-performance      0
28002                 11        10.0           onyx-jellyfish-of-wealth      0
29521                  1         0.0       festive-dalmatian-of-current      0
29867                 11        10.0              precious-tangible-cow      0

[84 rows x 4 columns]

In [219]:
df_posts['post_count_ge_2_flag'] = (df_posts['posts_fetch_count'] >= 2).astype(int)
df_posts[['label', col, ]]

label  time_diff_min_max_post_avg_ge_3600_flag
0          0                                        1
3          0                                        1
8          0                                        1
9          0                                        1
10         0                                        1
...      ...                                      ...
30405      0                                        1
30407      0                                        1
30408      0                                        0
30413      0                                        1
30419      0                                        1

[9033 rows x 2 columns]

In [220]:
plot_binary_distribution_by_label(df_posts.query('post_count >= 2'), col)

In [221]:
sub_df = df_posts.query('post_count < 1')[['binary_label', 'time_diff_min_max_post_avg']].copy()
sub_df['time_diff_flag_bot'] = sub_df['time_diff_min_max_post_avg'] >= 3600 
corr = sub_df.corr().loc['time_diff_flag_bot', 'binary_label']

print(f'Correlation between time_diff_flag_bot and binary_label for users zero or one post: {round(corr, 2)}')

Correlation between time_diff_flag_bot and binary_label for users zero or one post: -0.24


#### 1.10.3 Comments and likes

What's the min max difference compare to the median?

In [222]:
# Aggregating the columns and adding them to df_posts
for col in ['posts_concat_likes', 'posts_concat_comments']:
    df = df_posts.explode(col)
    df[col] = df[col].astype(float)
    df_grouped = df.groupby('username').agg({col: ['median', 'min', 'max', 'std']}).reset_index().round(2)
    df_grouped.columns = ['username'] + ['_'.join(col).strip() for col in df_grouped.columns.values if col != 'username'][1:]

    df_posts = df_posts.merge(df_grouped, on='username', how='left').drop(col, axis=1)

username  post_count  is_private  \
0               adorable-jade-beluga        76.0         0.0   
1                gentle-crimson-wolf         6.0         0.0   
2      calculating-tiger-of-security        63.0         0.0   
3         gorgeous-nimble-sidewinder       334.0         0.0   
4             hopeful-flashy-giraffe       258.0         0.0   
...                              ...         ...         ...   
9028      attractive-naughty-boobook       159.0         0.0   
9029   crouching-phenomenal-toucanet         3.0         0.0   
9030  petite-tarantula-of-completion         1.0         0.0   
9031          perky-curious-elephant        44.0         0.0   
9032            loud-nondescript-elk     2,594.0         0.0   

                                 posts_concat_is_video  \
0     [1, 1, 1, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 1, 0, 1]   
1                                   [0, 0, 0, 0, 0, 0]   
2                 [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
3                 [0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0]   
4                 [0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1]   
...                                                ...   
9028  [0, 0, 0, 0, 1, 1, 0, 0, 0, 1, 1, 1, 0, 0, 0, 0]   
9029                                         [0, 0, 0]   
9030                                               [0]   
9031              [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
9032              [0, 0, 1, 0, 1, 0, 0, 0, 1, 0, 0, 0]   

                               posts_concat_video_views  \
0     [5919, 822, 1509, 0, 0, 0, 1728, 0, 0, 3396, 1...   
1                                    [0, 0, 0, 0, 0, 0]   
2                  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
3                [0, 36, 0, 0, 0, 42, 0, 0, 0, 0, 0, 0]   
4            [0, 0, 0, 0, 0, 0, 0, 9162, 0, 0, 0, 3449]   
...                                                 ...   
9028  [0, 0, 0, 0, 2530, 2802, 0, 0, 0, 4452, 1347, ...   
9029                                          [0, 0, 0]   
9030                                                [0]   
9031               [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
9032       [0, 0, 567, 0, 2196, 0, 0, 0, 2005, 0, 0, 0]   

                                   posts_concat_caption  label  binary_label  \
0     [no caption, no caption, no caption, no captio...      0             0   
1     [Photo by Noah Reed on May 29, 2020. May be an...      0             0   
2     [Photo shared by @bauzb0mb on December 09, 202...      0             0   
3     [Photo shared by B-ILL on January 17, 2022 tag...      0             0   
4     [Photo by Tim in Mombasa, Kenya with @_mbitu_,...      0             0   
...                                                 ...    ...           ...   
9028  [Photo by Tee FLii on January 14, 2022. May be...      0             0   
9029  [Photo by V i c t o r R o d r i g o 🐊 on Janua...      0             0   
9030  [Photo by Donnie Bryant on December 07, 2018. ...      0             0   
9031  [Photo shared by Jeremy Padilla on December 26...      0             0   
9032  [Photo shared by YEA I STILL RAP CUZZ on Janua...      0             0   

      posts_fetch_count  time_diff_min_max_post_seconds  \
0                    16                        73317786   
1                     6                        19170605   
2                    12                       161829657   
3                    12                         8203381   
4                    12                          777202   
...                 ...                             ...   
9028                 16                         5447431   
9029                  3                         7705967   
9030                  1                               0   
9031                 12                        27220335   
9032                 12                          770881   

      time_diff_min_max_post_avg  time_diff_min_max_post_avg_ge_3600_flag  \
0                        4582361                                        1   
1                        3195

In [224]:

# df_grouped = df_posts.explode(col).groupby('username').agg({col: ['median', 'min', 'max', 'std']}).reset_index().round(2)
# df_grouped.columns = ['username'] + ['_'.join(col).strip() for col in df_grouped.columns.values if col != 'username'][1:]
# df_posts = df_posts.merge(df_grouped, on='username', how='left').drop(col, axis=1)
# df_posts

In [225]:
# def agg_likes_comments(df, cols, agg_func):
#     for col in cols:
#         df_grouped = df.explode(col).groupby('username').agg({col: agg_func}).reset_index().round(2)
#         df_grouped.columns = ['username'] + ['_'.join(col).strip() for col in df_grouped.columns.values if col != 'username'][1:]
#         df = df.merge(df_grouped, on='username', how='left').drop(col, axis=1)
#     return df

# df_posts = agg_likes_comments(df_posts, ['posts_concat_likes', 'posts_concat_comments'], ['median', 'min', 'max', 'std'])
# df_posts.describe_column_by_colcat('posts_concat_likes_std')[0].reset_index().rename({'index': col}, axis=1)
# # df_posts.info()

In [226]:
# dfs = []
# og_col = 'posts_concat_likes_'
# for col in df_posts:
#     if og_col in col: 
#         df = df_posts.describe_column_by_colcat(col)[0].reset_index().rename({'index': col.replace(og_col, '')}, axis=1)
#         dfs.append(df)


# pd.concat(dfs, axis=1)

Seems like the bots generally have less likes than the legit users.

In [227]:
# dfs = []
# og_col = 'posts_concat_comments_'
# for col in df_posts:
#     if og_col in col: 
#         df = df_posts.describe_column_by_colcat(col)[0].reset_index().rename({'index': col.replace(og_col, '')}, axis=1)
#         dfs.append(df)


# pd.concat(dfs, axis=1)

In [228]:
# df_posts['posts_concat_comments_min'].describe()

#### 1.10.4 Is video and video views

In [229]:
df_posts_video = df_posts[['username', 'label', 'posts_concat_is_video', 'posts_concat_video_views']].explode(['posts_concat_is_video', 'posts_concat_video_views'])
df_posts_video['posts_concat_is_video'] = df_posts_video['posts_concat_is_video'].astype(int)
df_posts_video['posts_concat_video_views'] = df_posts_video['posts_concat_video_views'].astype(int)
no_views_vid = df_posts_video.query('posts_concat_is_video == 1 and posts_concat_video_views == 0').shape
print(f'Number of videos with no views: {no_views_vid[0]}')

Number of videos with no views: 25


In [230]:
for flag in (0, 1):
    display(df_posts_video.query(f'posts_concat_is_video == {flag}')['label'].value_counts())

0    48028
1    15724
3     4286
Name: label, dtype: int64

0    14965
3      233
1      230
Name: label, dtype: int64

share of bots with one, share with more than 1???

In [231]:
plot_binary_distribution_by_label(df_posts_video, 'posts_concat_is_video')

There is some differenciation between the legit users and the bots. About 20% of the legit users have video compared to the bots for which very few have one.

In [232]:
df_posts_video.query('posts_concat_is_video == 1').describe_column_by_colcat('posts_concat_video_views')[0]

all         0       1     3
count     15428     14965     230   233
mean      28504     29227    9819   525
std      334133    339231   15538   903
min           0         0       2     2
25%         198       199    1882    80
50%         979       979    5109   198
75%        8231      8476   10375   473
max    28141508  28141508  108805  6472

Those results are weirds, no chance bots have as much views as that

In [233]:
# plot(df_posts_video.query('posts_concat_is_video == 1'), 'posts_concat_video_views')

In [234]:
# def plot (df, col):
#     labels = df['label'].unique()

#     # create figure with 2 rows and 3 columns (top chart uses 3 columns)
#     fig = make_subplots(rows=2, cols=len(labels), 
#                     specs=[[{'rowspan': 1, 'colspan': len(labels)}] + [None for _ in range(len(labels)-1)],
#                         [{'rowspan': 1, 'colspan': 1} for label in labels]],
#                     subplot_titles=['All Labels'] + [f'Label {label}' for label in labels],
#                     x_title=f'X: {col.title()}',
#                     y_title=f'Y: Freq')


#     # Adding all data
#     fig.add_trace(go.Histogram(x=df[col], name='All Labels'), row=1, col=1)


#     # label subplots
#     for index, label in enumerate(labels):
#         label_df = df[df['label'] == label]
#         fig.add_trace(go.Histogram(x=label_df[col], name=str(label), nbinsx=10000), row=2, col=index+1)

#     fig.update_layout(height=800, title=f'Distribution of Labels by {col.title()}')


#     return fig


# plot(df_posts, 'posts_concat_likes_median')

In [235]:
# Aggreagating video and views columns only for video 
agg = {'posts_concat_is_video': ['sum'],
       'posts_concat_video_views': ['sum', 'min', 'max', 'median']}
df_posts_video = df_posts_video.query('posts_concat_is_video == 1').groupby('username').agg(agg).reset_index().round(2)
df_posts_video.columns = ['username'] + ['_'.join(col).strip() for col in df_posts_video.columns.values if col != 'username'][1:]

# Merging and replacing null values (no video/views) by 0
df_posts = df_posts.merge(df_posts_video, on='username', how='left').drop(['posts_concat_is_video', 'posts_concat_video_views'], axis=1)
for col in ['posts_concat_is_video_sum', 'posts_concat_video_views_sum', 'posts_concat_video_views_min', 'posts_concat_video_views_max', 'posts_concat_video_views_median']:
    df_posts[col] = df_posts[col].fillna(0)

df_posts.head()

username  post_count  is_private  \
0           adorable-jade-beluga        76.0         0.0   
1            gentle-crimson-wolf         6.0         0.0   
2  calculating-tiger-of-security        63.0         0.0   
3     gorgeous-nimble-sidewinder       334.0         0.0   
4         hopeful-flashy-giraffe       258.0         0.0   

                                posts_concat_caption  label  binary_label  \
0  [no caption, no caption, no caption, no captio...      0             0   
1  [Photo by Noah Reed on May 29, 2020. May be an...      0             0   
2  [Photo shared by @bauzb0mb on December 09, 202...      0             0   
3  [Photo shared by B-ILL on January 17, 2022 tag...      0             0   
4  [Photo by Tim in Mombasa, Kenya with @_mbitu_,...      0             0   

   posts_fetch_count  time_diff_min_max_post_seconds  \
0                 16                        73317786   
1                  6                        19170605   
2                 12                       161829657   
3                 12                         8203381   
4                 12                          777202   

   time_diff_min_max_post_avg  time_diff_min_max_post_avg_ge_3600_flag  \
0                     4582361                                        1   
1                     3195100                                        1   
2                    13485804                                        1   
3                      683615                                        1   
4                       64766                                        1   

   post_count_ge_2_flag  posts_concat_likes_median  posts_concat_likes_min  \
0                     1                      144.5                    40.0   
1                     1                      197.5                   127.0   
2                     1                       59.0                    14.0   
3                     1                       12.5                     3.0   
4                     1                      680.0                   409.0   

   posts_concat_likes_max  posts_concat_likes_std  \
0                   356.0                   93.35   
1                   246.0                   50.51   
2                   136.0                   43.38   
3                    36.0                    9.18   
4                 1,625.0                  391.66   

   posts_concat_comments_median  posts_concat_comments_min  \
0                          11.0                        2.0   
1                           2.0                        1.0   
2                           4.0                        0.0   
3                           1.0                        0.0   
4                          69.0                       29.0   

   posts_concat_comments_max  posts_concat_comments_std  \
0                       94.0                      26.07   
1                        6.0                       1.76   
2                       31.0                       9.01   
3                        5.0                       1.88   
4                       95.0                       21.1   

   posts_concat_is_video_sum  posts_concat_video_views_sum  \
0                        9.0                      18,846.0   
1                        0.0                           0.0   
2                        0.0                           0.0   
3                        2.0                          78.0   
4                        2.0                      12,611.0   

   posts_concat_video_views_min  posts_concat_video_views_max  \
0                         749.0                       5,919.0   
1                           0.0                           0.0   
2                           0.0                           0.0   
3                          36.0                          42.0   
4                       3,449.0                       9,162.0   

   posts_concat_video_views_median  
0                          1,509.0  
1                              0.0  
2                          

#### 1.10.5 Caption

In [236]:
x = 'Photo by Noah Reed on May 29, 2020. May be an image of one or more people, people standing and indoor.'

[x for x in x.split('.') if 'May be an image of' in x][0]

' May be an image of one or more people, people standing and indoor'

In [237]:
df_posts_caption = df_posts[['username', 'label', 'posts_concat_caption']].explode('posts_concat_caption')

def doit(caption): 
    if caption == 'no caption':  
        return ['no caption']
    

    elements = ''.join([x.replace(' May be an image of', '') for x in caption.split('.') if 'May be an image of' in x])
    if 'text that says' in elements: 
        elements = elements[:elements.index('text that says')]
    
    return [x.strip() for x in re.split(', | and ', elements) if 'text that says' not in x]


df_posts_caption['image_of'] = df_posts_caption['posts_concat_caption'].apply(lambda x: doit(x))
df_posts_caption = df_posts_caption.explode('image_of').query('image_of != ""')
df_posts_caption

username  label  \
0     adorable-jade-beluga      0   
0     adorable-jade-beluga      0   
0     adorable-jade-beluga      0   
0     adorable-jade-beluga      0   
0     adorable-jade-beluga      0   
...                    ...    ...   
9032  loud-nondescript-elk      0   
9032  loud-nondescript-elk      0   
9032  loud-nondescript-elk      0   
9032  loud-nondescript-elk      0   
9032  loud-nondescript-elk      0   

                                   posts_concat_caption            image_of  
0                                            no caption          no caption  
0                                            no caption          no caption  
0                                            no caption          no caption  
0                                            no caption          no caption  
0                                            no caption          no caption  
...                                                 ...                 ...  
9032  Photo by YEA I STILL RAP CUZZ on January 13, 2...                food  
9032                                         no caption          no caption  
9032  Photo by YEA I STILL RAP CUZZ on January 11, 2...  one or more people  
9032  Photo by YEA I STILL RAP CUZZ on January 10, 2...  one or more people  
9032  Photo by YEA I STILL RAP CUZZ on January 10, 2...  one or more people  

[123512 rows x 4 columns]

In [238]:
sub_df = df_posts_caption.copy()
top_n = 45
labels = sub_df['label'].unique()


print(len(labels))

# create a dictionary to map label to subplot index
label_subplot_dict = {label: i+1 for i, label in enumerate(labels)}

# create figure with 2 rows and 3 columns (top chart uses 3 columns)
fig = make_subplots(rows=2, cols=len(labels), 
                specs=[[{'rowspan': 1, 'colspan': len(labels)}] + [None, None],
                    [{'rowspan': 1, 'colspan': 1} for label in labels]],
                    subplot_titles=['All Labels'] + [f'Label {label}' for label in labels],
                y_title='Your master y-title')#, shared_yaxes=True)


# Adding all data regardless of label
data = sub_df['image_of'].value_counts(normalize=True).multiply(100).round(2).sort_values(ascending=False).head(top_n).to_dict()
data.update({'other': round(100 - sum(data.values()), 2)})
fig.add_trace(go.Bar(name='All Labels', 
                        x=list(data.keys()), 
                        y=list(data.values()), 
                        text=[str(value) for value in data.values()]), 
                row=1, col=1)


# subplot_titles=[f'All Labels: n={no:,} / y={yes:,}']
# label subplots
for label in sub_df['label'].unique():
    print(label)
    data = sub_df.query(f'label == {label}')['image_of'].value_counts(normalize=True).multiply(100).round(2).sort_values(ascending=False).head(top_n // 3).to_dict()
    data.update({'other': round(100 - sum(data.values()), 2)})
    fig.add_trace(go.Bar(name='All Labels', 
                            x=list(data.keys()), 
                            y=list(data.values()), 
                            text=[str(value) for value in data.values()]), 
                            
                    row=2, col=label_subplot_dict[label])

fig.update_layout(height=800, 
                    title=f'Distribution of Labels by domain category')

# subplot_titles += [''] + [''] # This is for the x and y main axis titles
# fig.update_layout(annotations=[{'text': name} for name in subplot_titles])

3
0
1
3


It's interesting to see how most of the legit users have no captioin where the bot almost have none

In [239]:
top_elements = []
for x in (0, 1, 3):
    top_elements += list(df_posts_caption.query(f'label == {x}')['image_of'].value_counts().head(10).index)

set(top_elements)

{'1 person',
 'beard',
 'body of water',
 'car',
 'footwear',
 'indoor',
 'long hair',
 'no caption',
 'one or more people',
 'outdoors',
 'people playing football',
 'people standing',
 'road',
 'standing',
 'tattoo',
 'text',
 'wrist watch'}

In [240]:
df_posts = df_posts.merge(df_posts_caption.groupby('username').agg({'image_of': lambda x: list(x)}).reset_index(), on='username', how='left')

for element in set(top_elements): 
    element = element.replace(' ', '_')
    df_posts[element + '_in_caption_count'] = df_posts['image_of'].apply(lambda x: x.count(element) if isinstance(x, list) else x)
    df_posts[element + '_in_caption'] = (df_posts[element + '_in_caption_count'] > 0).astype(int)

df_posts = df_posts.drop(['image_of', 'posts_concat_caption'], axis=1)
df_posts.head()

username  post_count  is_private  label  binary_label  \
0           adorable-jade-beluga        76.0         0.0      0             0   
1            gentle-crimson-wolf         6.0         0.0      0             0   
2  calculating-tiger-of-security        63.0         0.0      0             0   
3     gorgeous-nimble-sidewinder       334.0         0.0      0             0   
4         hopeful-flashy-giraffe       258.0         0.0      0             0   

   posts_fetch_count  time_diff_min_max_post_seconds  \
0                 16                        73317786   
1                  6                        19170605   
2                 12                       161829657   
3                 12                         8203381   
4                 12                          777202   

   time_diff_min_max_post_avg  time_diff_min_max_post_avg_ge_3600_flag  \
0                     4582361                                        1   
1                     3195100                                        1   
2                    13485804                                        1   
3                      683615                                        1   
4                       64766                                        1   

   post_count_ge_2_flag  posts_concat_likes_median  posts_concat_likes_min  \
0                     1                      144.5                    40.0   
1                     1                      197.5                   127.0   
2                     1                       59.0                    14.0   
3                     1                       12.5                     3.0   
4                     1                      680.0                   409.0   

   posts_concat_likes_max  posts_concat_likes_std  \
0                   356.0                   93.35   
1                   246.0                   50.51   
2                   136.0                   43.38   
3                    36.0                    9.18   
4                 1,625.0                  391.66   

   posts_concat_comments_median  posts_concat_comments_min  \
0                          11.0                        2.0   
1                           2.0                        1.0   
2                           4.0                        0.0   
3                           1.0                        0.0   
4                          69.0                       29.0   

   posts_concat_comments_max  posts_concat_comments_std  \
0                       94.0                      26.07   
1                        6.0                       1.76   
2                       31.0                       9.01   
3                        5.0                       1.88   
4                       95.0                       21.1   

   posts_concat_is_video_sum  posts_concat_video_views_sum  \
0                        9.0                      18,846.0   
1                        0.0                           0.0   
2                        0.0                           0.0   
3                        2.0                          78.0   
4                        2.0                      12,611.0   

   posts_concat_video_views_min  posts_concat_video_views_max  \
0                         749.0                       5,919.0   
1                           0.0                           0.0   
2                           0.0                           0.0   
3                          36.0                          42.0   
4                       3,449.0                       9,162.0   

   posts_concat_video_views_median  footwear_in_caption_count  \
0                          1,509.0                        0.0   
1                              0.0                        0.0   
2                              0.0                        0.0   
3                             39.0                        0.0   
4                          6,305.5                        0.0   

   footwear_in_caption  wrist_watch_in_caption_count  wrist_watch_in_caption  \
0   

In [241]:
df_posts[[col for col in df_posts if col not in df_posts.select_dtypes(['int', 'float']).columns]].info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 9033 entries, 0 to 9032
Data columns (total 1 columns):
 #   Column    Non-Null Count  Dtype 
---  ------    --------------  ----- 
 0   username  9033 non-null   object
dtypes: object(1)
memory usage: 141.1+ KB


In [244]:
df_main = df_main.merge(df_posts, on='username', how='left')
df_main

username  \
0                adorable-jade-beluga   
1           hysterical-glistening-bee   
2                  little-crafty-mink   
3                 gentle-crimson-wolf   
4                festive-uppish-leech   
...                               ...   
30415      attentive-mongoose-of-hail   
30416    resourceful-thistle-toucanet   
30417           glorious-zippy-agouti   
30418  hopping-stallion-of-conversion   
30419            loud-nondescript-elk   

                                               biography  \
0      ⁣⁣28 🇩🇪 🇪🇸 \nCapricorn 🐐 \nDallas TX📍Outside 🍾...   
1      “Moving at a pace slow for some but fast for o...   
2                                              New Page.   
3                                             • 9/26 💘 •   
4                                           Stay mad bum   
...                                                  ...   
30415                              Yours truly, The boy🗽   
30416  I’m Yung Bolt\nGo Giants 🔵🔴 #lfgm🍎 \nMMG and J...   
30417  NICE GIRL 🇺🇸🧚\n💖Sweet booty | 📹Content Creator...   
30418  Love tattoo\nHave no boyfriend for a long time...   
30419                                  LINK'S IN BIO👇🏾👇🏾   

                                      biography_wo_emoji biography_emoji  \
0      ⁣⁣28   \nCapricorn  \nDallas TXOutside \n“Her ...        🇩🇪🇪🇸🚫🍾📍🐐   
1      “Moving at a pace slow for some but fast for o...             ⬇️🚨   
2                                              New Page.                   
3                                              • 9/26  •               💘   
4                                           Stay mad bum                   
...                                                  ...             ...   
30415                               Yours truly, The boy               🗽   
30416  I’m Yung Bolt\nGo Giants  #lfgm \nMMG and JIDI...             🔵🔴🍎   
30417  NICE GIRL \nSweet booty | Content Creator\nI h...      👇🏼😌📹👿🔞🇺🇸💖🧚   
30418  Love tattoo\nHave no boyfriend for a long time...              🍌👇   
30419                                      LINK'S IN BIO              👇🏾   

       biography_emoji_count  biography_emoji_count_distinct  follow_count  \
0                        6.0                             6.0       3,164.0   
1                        2.0                             2.0         114.0   
2                        0.0                             0.0         204.0   
3                        1.0                             1.0         211.0   
4                        0.0                             0.0           0.0   
...                      ...                             ...           ...   
30415                    1.0                             1.0         278.0   
30416                    3.0                             3.0       1,251.0   
30417                    9.0                             8.0           0.0   
30418                    3.0                             2.0           7.0   
30419                    2.0                             1.0       2,733.0   

       follower_count pronouns           domain  \
0             4,676.0     None  mintyswraps.com   
1                52.0     None      youtube.com   
2               422.0     None             None   
3               586.0     None             None   
4                 0.0     None             None   
...               ...      ...              ...   
30415           330.0     None     fanofno1.com   
30416           373.0     None             None   
30417           253.0     None        linkr.bio   
30418           918.0     None        linkr.bio   
30419        15,392.0     None          solo.to   

                                                 comment  \
0                          Bucks finna have a repeat 🏆 👀   
1                           CRAZY EYES GOT MOVES LOL 🤣🤣😭   
2                            Flight is gonna be heated 😂   
3      Someone forgot to tell the warriors they had a...   
4                          Klay is back scary hourss

### Done but need to add above
--- 

In [245]:
df_main.to_sql('main_after_univariate', con, if_exists='replace', index=False)

30420

---

In [ ]:
# import matplotlib.cm
# cmap = matplotlib.cm.get_cmap('Reds')
def left_subtract(l1,l2):
    lst = []
    for i in l1:
        if i not in l2:
            lst.append(i)
    return lst
def data_suggestions(data):
    """
    Modified by Ram Seshadri. Original idea for data suggestions module was a Kaggler.
    Many thanks to: https://www.kaggle.com/code/itkin16/catboost-on-gpu-baseline
    """
    maxx = []
    minn = []
    all_cols = list(data)
    cat_cols1 = data.select_dtypes(include='object').columns.tolist()
    cat_cols2 = data.select_dtypes(include='category').columns.tolist()
    cat_cols = list(set(cat_cols1+cat_cols2))
    ### The next line may look odd but due to different versions of pandas which
    ### treat the definition of float differently, I am forced to use this. Don't change it.
    num_cols = data.select_dtypes(include='float16').columns.tolist() + data.select_dtypes(
                    include='float32').columns.tolist() + data.select_dtypes(include='float64').columns.tolist()
    non_num_cols = left_subtract(all_cols, num_cols)
    for i in data.columns:
        if i not in cat_cols:
            ### for float and integer, no need to calculate this ##
            minn.append(0)
        else:
            minn.append(data[i].value_counts().min())
    length = len(data)
    nunik = data.nunique()
    nulls = data.isna().sum()
    df = pd.DataFrame(
        {
         #'column': list(data),
        'Nuniques': nunik,
         'NuniquePercent': (100*(nunik/length)),
         'dtype': data.dtypes,
         'Nulls' : nulls,
         'Nullpercent' : 100*(nulls/length),
         'Value counts Min':minn
        },
        columns = ['Nuniques', 'dtype','Nulls','Nullpercent', 'NuniquePercent',
                       'Value counts Min'])
    newcol = 'Data cleaning improvement suggestions'
    print('%s. Complete them before proceeding to ML modeling.' %newcol)
    mixed_cols = [col for col in data.columns if len(data[col].apply(type).value_counts()) > 1]
    df[newcol] = ''
    df['first_comma'] = ''
    if len(cat_cols) > 0:
        mask0 = df['dtype'] == 'object'
        mask1 = df['Value counts Min']/df['Nuniques'] <= 0.05
        mask4 = df['dtype'] == 'category'
        df.loc[mask0&mask1,newcol] += df.loc[mask0&mask1,'first_comma'] + 'combine rare categories'
        df.loc[mask4&mask1,newcol] += df.loc[mask4&mask1,'first_comma'] + 'combine rare categories'
        df.loc[mask0&mask1,'first_comma'] = ', '
        df.loc[mask4&mask1,'first_comma'] = ', '
    mask2 = df['Nulls'] > 0
    df.loc[mask2,newcol] += df.loc[mask2,'first_comma'] + 'fill missing'
    df.loc[mask2,'first_comma'] = ", "
    mask3 = df['Nuniques'] == 1
    df.loc[mask3,newcol] += df.loc[mask3,'first_comma'] + 'invariant values: drop'
    df.loc[mask3,'first_comma'] = ", "
    if len(non_num_cols) > 0:
        for x in non_num_cols:
            if df.loc[x, 'NuniquePercent'] == 100:
                df.loc[x, newcol] += df.loc[x,'first_comma'] + 'possible ID column: drop'
                df.loc[x,'first_comma'] = ", "
    mask5 = df['Nullpercent'] >= 90
    df.loc[mask5,newcol] += df.loc[mask5,'first_comma'] + 'very high nulls percent: drop'
    df.loc[mask5,'first_comma'] = ", "
    #### check for infinite values here #####
    inf_cols1 = np.array(num_cols)[[(data.loc[(data[col] == np.inf)]).shape[0]>0 for col in num_cols]].tolist()
    inf_cols2 = np.array(num_cols)[[(data.loc[(data[col] == -np.inf)]).shape[0]>0 for col in num_cols]].tolist()
    inf_cols = list(set(inf_cols1+inf_cols2))
    ### Check for infinite values in columns #####
    if len(inf_cols) > 0:
        for x in inf_cols:
            df.loc[x,newcol] += df.loc[x,'first_comma'] + 'infinite values: drop'
            df.loc[x,'first_comma'] = ", "
    #### Check for skewed float columns #######
    skew_cols1 = np.array(num_cols)[[(np.abs(np.round(data[col].skew(), 1)) > 1
                    ) & (np.abs(np.round(data[col].skew(), 1)) <= 5) for col in num_cols]].tolist()
    skew_cols2 = np.array(num_cols)[[(np.abs(np.round(data[col].skew(), 1)) > 5) for col in num_cols]].tolist()
    skew_cols = list(set(skew_cols1+skew_cols2))
    ### Check for skewed values in columns #####
    if len(skew_cols1) > 0:
        for x in skew_cols1:
            df.loc[x,newcol] += df.loc[x,'first_comma'] + 'skewed: cap or drop outliers'
            df.loc[x,'first_comma'] = ", "
    if len(skew_cols2) > 0:
        for x in skew_cols2:
            df.loc[x,newcol] += df.loc[x,'first_comma'] + 'highly skewed: drop outliers or do box-cox transform'
            df.loc[x,'first_comma'] = ", "
    ##### Do the same for mixed dtype columns - they must be fixed! ##
    if len(mixed_cols) > 0:
        for x in mixed_cols:
            df.loc[x,newcol] += df.loc[x,'first_comma'] + 'fix mixed data types'
            df.loc[x,'first_comma'] = ", "
    df.drop('first_comma', axis=1, inplace=True)
    return df
###################################################################################
def data_cleaning_suggestions(df):
    """
    This is a simple program to give data cleaning and improvement suggestions in class AV.
    Make sure you send in a dataframe. Otherwise, this will give an error.
    """
    if isinstance(df, pd.DataFrame):
        dfx = data_suggestions(df)
        all_rows = dfx.shape[0]
        ax = dfx.head(all_rows).style.background_gradient()  
        display(ax);
    else:
        print("Input must be a dataframe. Please check input and try again.")
###################################################################################

In [ ]:
# exclude_cols = ['username', 'biography', 'follow_count'] + [col for col in df_main.columns if isinstance(df_main.loc[0, col], (dict, list))]
data_cleaning_suggestions(df_main)

In [ ]:
df_main.to_sql('main_after_univariate', con, if_exists='replace', index=False)

os.system('say "Data Cleaning Done"')

In [ ]:
asdf

## Above this is new clean code and markdown formatting where below is old code kinda eh formatted

### 
---

### 1.x Comment time difference WHATS THE AVERAG DIFFERENCE BETWEEN EACH POST? COULD BE UPLOADED SUPER FAST

In [ ]:
# def round_or_int(val, **kwargs): 
#     if pd.isna(val): 
#         return val
#     elif val == int(val): 
#         return int(val) 
#     else:
#         return round(val, ndigits=kwargs['ndigits'])

# def calculate_posts_time_diff_btw_each(date_concat): 
#     if pd.isna(date_concat): 
#         return date_concat
#     dates = [pd.to_datetime(date) for date in date_concat.split(',')]
#     dates = sorted(list(set(dates)))[:12]
#     dates_diff = pd.Series(dates).diff().dt.seconds.dropna().reset_index(drop=True)
#     dates_diff_summary = dates_diff.describe().apply(round_or_int, ndigits=2).to_dict()
#     dates_diff_summary.update({'dates_diff': dates_diff.tolist(),
#                                'unique_values': len(set(dates_diff)),
#                                'total_values': len(dates_diff)
#                                })

#     # display(pd.DataFrame({i:[j] for i, j in dates_diff_summary.items()}))
#     dates_diff_summary = {'dates_diff_' + i:j for i, j in dates_diff_summary.items()}
#     return dates_diff_summary

# df_main['posts_diff_btw_each_summary_seconds'] = df_main['posts_concat_posted_time'].parallel_apply(calculate_posts_time_diff_btw_each)
# # calculate_posts_time_diff_btw_each(df_main.loc[1, 'posts_concat_posted_time'])
# df_posts_diff_btw_each_summary = pd.json_normalize(df_main['posts_diff_btw_each_summary_seconds'])

In [ ]:
# df_main = pd.concat([df_main, df_posts_diff_btw_each_summary], axis=1)
# df_main.head()

In [ ]:
# sub_df = df_main[['dates_diff_follows_pattern', 'post_count', 'label']]

# fig = px.scatter_matrix(sub_df, color='label', title='Pairplot')
# sv.save_plotly_fig(fig)

In [ ]:
# # Describing column for each label
# sub_df, fig = df_main.describe_column_by_label('dates_diff_50%')

# print('dates_diff_50%: ')
# display(sub_df.style.format('{:,}'))
# fig

### Investigate

In [ ]:
# adsf

In [ ]:
usernames = df_main.query('time_diff_min_max_post_avg > 1000000 and label > 0')['username']
# df_main_bu.query('username in @usernames')
sl.show_user_summary(usernames=usernames)

In [ ]:
df_posts_video.query('posts_concat_is_video == 1 and label > 0')

In [ ]:
column = 'comment_likes'

# display(df_main.head(50))
username = 'unselfish-tangible-silkworm'
# print(sl.load_table('select '))
# print(username)

display(sl.load_labels(include_all=True).query('username == @username'))
# display(sl.load_table('username_mapping').query('cooler_name == @username'))
# df_main.query('username == @username')


# sub_df.query('comment_likes > 1000 and label > 0')
df_main_bu.query('username == @username')

In [ ]:
# df_main.query('biography.str.contains("skate") and label > 0')

In [ ]:
# df_main.query('username == "axiomatic-merciful-mayfly"')

### Done investigating

## 2.0 Multi variate analysis - Past this point the data is entirely clean and ready for ML.

Questions to answer:
* Try to see for how long the bot profile have existed (number of followers? posts?) against private. Is it because they live too long that they go private to not be banned?
* Check the correlation of features with embed enabled

In [ ]:
df_main = pd.read_sql_query('select * from main_after_univariate', con)
df_main

In [ ]:
try: 
    df_main = df_main.drop('comment_emoji', axis=1)
except Exception as e:
    print(e)

In [ ]:
# # Removing columns for now as there are way too many and feel overwhelmed
# cols_to_remove = ['posts_sum', 'posts_avg', 'posts_max', 'posts_min', 'posts_con', 'dates_dif']
# cols_to_remove = [col for col in df_main.columns if any([x in col for x in cols_to_remove])] + ['biography', 'biography_wo_emoji', 'biography_emoji', 'domain', 'comment', 'comment_wo_emoji',
#                                                                                                 'comment_emoji', 'labelling_technique', 'posts_diff_btw_each_summary_seconds']
# cols_to_keep = [col for col in df_main.columns if col not in cols_to_remove]

# df_main = df_main[cols_to_keep]
# df_main.head()

### 2.1 Pair plot & correlation

In [ ]:
# a = []
# for x in ['username', 'biography_emoji_count', 'biography_emoji_count_distinct',
#        'follow_count', 'follower_count', 'pronouns', 'domain',
#        'comment_likes', 'comment_emoji_count', 'comment_emoji_count_distinct',
#        'comment_time_difference', 'post_count', 'video_count',
#        'highlight_reel_count', 'hide_like_and_view_counts', 'has_guides',
#        'has_clips', 'is_private', 'is_embeds_disabled', 'is_joined_recently',
#        'is_professional_account', 'is_business_account',
#        'should_show_public_contacts', 'posts_days_diff', 'posts_hours_diff',
#        'is_verified', 'label', 'labelling_technique', 'binary_label',
#        'outlier', 'comment_grams_count', 'comment_length',
#        'comment_word_count', 'biography_grams_count', 'biography_length',
#        'biography_word_count', 'biography_linebreak_count',
#        'pronouns_na_flag']: 
#     print(x + '\t\t\t\t\t', end='\r')
#     if input() == 'y': 
#         a.append(x)






In [ ]:
corr_matrix.iloc[-1] = np.nan

In [ ]:
df_main.corr() > 0.8

In [ ]:
corr_matrix = df_main.corr()
corr_matrix.iloc[-1] = np.nan

# fig = px.imshow(corr_matrix,
#                 color_continuous_scale='RdBu',
#                 x=corr_matrix.columns,
#                 y=corr_matrix.columns)
# fig.update_layout(title='Correlation Matrix',
#                   width=600, height=600)
# fig.update_traces(showscale=True)
# fig.show()


In [ ]:
# df_main.outlier.value_counts()fig = px.imshow(corr_matrix,
#                 color_continuous_scale='RdBu',
#                 labels=dict(x='Variable', y='Variable', color='Correlation'),
#                 x=corr_matrix.columns,
#                 y=corr_matrix.columns)
# fig.update_layout(title='Correlation Matrix',
#                   width=600, height=600,
#                   margin=dict(l=40, r=40, b=40, t=40),
#                   paper_bgcolor='white')
# fig.update_traces(showscale=True)
# fig.show()


In [ ]:
# df_main[cols + ['label', 'outlier']].query('outlier == ""')

In [ ]:

# cols = ['follow_count', 'follower_count', 'post_count', 'video_count', 'is_private', 'posts_hours_diff']
# sns.pairplot(df_main[cols + ['label', 'outlier']].query('label > 0'), 
#              hue="label", )

### 2.x ChatGPT charts

In [ ]:
fig = px.scatter(df_main, x='follow_count', y='follower_count', trendline='ols',
                 title='Follower Count vs. Follow Count')
fig.update_layout(xaxis_title='Follow Count', yaxis_title='Follower Count')
fig.show()


In [ ]:
import plotly.graph_objs as go
from plotly.subplots import make_subplots

def plot (df_main, xcol, ycol):
       labels = df_main['label'].unique()

       # create a dictionary to map label to subplot index
       label_subplot_dict = {label: i+1 for i, label in enumerate(labels)}

       # create figure with 2 rows and 3 columns (top chart uses 3 columns)
       fig = make_subplots(rows=2, cols=len(labels), 
                     specs=[[{'rowspan': 1, 'colspan': len(labels)}] + [None for _ in range(len(labels)-1)],
                            [{'rowspan': 1, 'colspan': 1} for label in labels]],
                     subplot_titles=['All Labels'] + [f'Label {label}' for label in labels],
                     x_title=f'X: {xcol.title()}',
                     y_title=f'Y: {ycol.title()}')

       # Adding all data
       if xcol != None and ycol != None:
              fig.add_trace(go.Histogram(x=df_main[xcol], name='All Labels'), row=1, col=1)
       elif xcol !=  None and ycol == None: 
              fig.add_trace(go.Scatter(x=df_main[xcol], y=df_main[ycol], 
                                   mode='markers', name='All Labels'), row=1, col=1)

       # label subplots
       for label in df_main['label'].unique():
              label_df = df_main[df_main['label'] == label]
              if isinstance(xcol, str) and isinstance(ycol, str):
                     fig.add_trace(go.Scatter(
                                                 x=label_df[xcol], 
                                                 y=label_df[ycol], 
                                                 mode='markers', 
                                                 name=label, 
                                                 marker_color= plotly_kwargs['color_discrete_sequence'][int(label)]), 
                                   row=2, col=label_subplot_dict[label])

              elif xcol is not None and ycol is None:
                     fig.add_trace(go.Histogram(x=label_df[xcol], name=label), row=2, col=label_subplot_dict[label])

       fig.update_layout(height=800, title=f'Distribution of Labels by {xcol.title()} and {ycol.title()}')


       return fig


plot(df_main.query('label > -1'), 'follow_count', 'follower_count')

In [ ]:
print('''end=




{
	"name": "ValueError",
	"message": "\n    Invalid value of type 'numpy.int64' received for the 'name' property of scatter\n        Received value: 0\n\n    The 'name' property is a string and must be specified as:\n      - A string\n      - A number that will be converted to a string",
	"stack": "\u001b[0;31m---------------------------------------------------------------------------\u001b[0m\n\u001b[0;31mValueError\u001b[0m                                Traceback (most recent call last)\n\u001b[0;32m/var/folders/52/s1w1p2q558xfjlyyyjlbfphr0000gn/T/ipykernel_10108/1530464244.py\u001b[0m in \u001b[0;36m<cell line: 46>\u001b[0;34m()\u001b[0m\n\u001b[1;32m     44\u001b[0m \u001b[0;34m\u001b[0m\u001b[0m\n\u001b[1;32m     45\u001b[0m \u001b[0;34m\u001b[0m\u001b[0m\n\u001b[0;32m---> 46\u001b[0;31m \u001b[0mplot\u001b[0m\u001b[0;34m(\u001b[0m\u001b[0mdf_main\u001b[0m\u001b[0;34m.\u001b[0m\u001b[0mquery\u001b[0m\u001b[0;34m(\u001b[0m\u001b[0;34m'label > -1'\u001b[0m\u001b[0;34m)\u001b[0m\u001b[0;34m,\u001b[0m \u001b[0;34m'follow_count'\u001b[0m\u001b[0;34m,\u001b[0m \u001b[0;34m'follower_count'\u001b[0m\u001b[0;34m)\u001b[0m\u001b[0;34m\u001b[0m\u001b[0;34m\u001b[0m\u001b[0m\n\u001b[0m\n\u001b[0;32m/var/folders/52/s1w1p2q558xfjlyyyjlbfphr0000gn/T/ipykernel_10108/1530464244.py\u001b[0m in \u001b[0;36mplot\u001b[0;34m(df_main, xcol, ycol)\u001b[0m\n\u001b[1;32m     27\u001b[0m               \u001b[0mlabel_df\u001b[0m \u001b[0;34m=\u001b[0m \u001b[0mdf_main\u001b[0m\u001b[0;34m[\u001b[0m\u001b[0mdf_main\u001b[0m\u001b[0;34m[\u001b[0m\u001b[0;34m'label'\u001b[0m\u001b[0;34m]\u001b[0m \u001b[0;34m==\u001b[0m \u001b[0mlabel\u001b[0m\u001b[0;34m]\u001b[0m\u001b[0;34m\u001b[0m\u001b[0;34m\u001b[0m\u001b[0m\n\u001b[1;32m     28\u001b[0m               \u001b[0;32mif\u001b[0m \u001b[0misinstance\u001b[0m\u001b[0;34m(\u001b[0m\u001b[0mxcol\u001b[0m\u001b[0;34m,\u001b[0m \u001b[0mstr\u001b[0m\u001b[0;34m)\u001b[0m \u001b[0;32mand\u001b[0m \u001b[0misinstance\u001b[0m\u001b[0;34m(\u001b[0m\u001b[0mycol\u001b[0m\u001b[0;34m,\u001b[0m \u001b[0mstr\u001b[0m\u001b[0;34m)\u001b[0m\u001b[0;34m:\u001b[0m\u001b[0;34m\u001b[0m\u001b[0;34m\u001b[0m\u001b[0m\n\u001b[0;32m---> 29\u001b[0;31m                      fig.add_trace(go.Scatter(\n\u001b[0m\u001b[1;32m     30\u001b[0m                                                  \u001b[0mx\u001b[0m\u001b[0;34m=\u001b[0m\u001b[0mlabel_df\u001b[0m\u001b[0;34m[\u001b[0m\u001b[0mxcol\u001b[0m\u001b[0;34m]\u001b[0m\u001b[0;34m,\u001b[0m\u001b[0;34m\u001b[0m\u001b[0;34m\u001b[0m\u001b[0m\n\u001b[1;32m     31\u001b[0m                                                  \u001b[0my\u001b[0m\u001b[0;34m=\u001b[0m\u001b[0mlabel_df\u001b[0m\u001b[0;34m[\u001b[0m\u001b[0mycol\u001b[0m\u001b[0;34m]\u001b[0m\u001b[0;34m,\u001b[0m\u001b[0;34m\u001b[0m\u001b[0;34m\u001b[0m\u001b[0m\n\n\u001b[0;32m/opt/homebrew/Caskroom/miniforge/base/envs/main_env/lib/python3.8/site-packages/plotly/graph_objs/_scatter.py\u001b[0m in \u001b[0;36m__init__\u001b[0;34m(self, arg, cliponaxis, connectgaps, customdata, customdatasrc, dx, dy, error_x, error_y, fill, fillcolor, fillpattern, groupnorm, hoverinfo, hoverinfosrc, hoverlabel, hoveron, hovertemplate, hovertemplatesrc, hovertext, hovertextsrc, ids, idssrc, legendgroup, legendgrouptitle, legendrank, line, marker, meta, metasrc, mode, name, opacity, orientation, selected, selectedpoints, showlegend, stackgaps, stackgroup, stream, text, textfont, textposition, textpositionsrc, textsrc, texttemplate, texttemplatesrc, uid, uirevision, unselected, visible, x, x0, xaxis, xcalendar, xhoverformat, xperiod, xperiod0, xperiodalignment, xsrc, y, y0, yaxis, ycalendar, yhoverformat, yperiod, yperiod0, yperiodalignment, ysrc, **kwargs)\u001b[0m\n\u001b[1;32m   3210\u001b[0m         \u001b[0m_v\u001b[0m \u001b[0;34m=\u001b[0m \u001b[0mname\u001b[0m \u001b[0;32mif\u001b[0m \u001b[0mname\u001b[0m \u001b[0;32mis\u001b[0m \u001b[0;32mnot\u001b[0m \u001b[0;32mNone\u001b[0m \u001b[0;32melse\u001b[0m \u001b[0m_v\u001b[0m\u001b[0;34m\u001b[0m\u001b[0;34m\u001b[0m\u001b[0m\n\u001b[1;32m   3211\u001b[0m         \u001b[0;32mif\u001b[0m \u001b[0m_v\u001b[0m \u001b[0;32mis\u001b[0m \u001b[0;32mnot\u001b[0m \u001b[0;32mNone\u001b[0m\u001b[0;34m:\u001b[0m\u001b[0;34m\u001b[0m\u001b[0;34m\u001b[0m\u001b[0m\n\u001b[0;32m-> 3212\u001b[0;31m             \u001b[0mself\u001b[0m\u001b[0;34m[\u001b[0m\u001b[0;34m\"name\"\u001b[0m\u001b[0;34m]\u001b[0m \u001b[0;34m=\u001b[0m \u001b[0m_v\u001b[0m\u001b[0;34m\u001b[0m\u001b[0;34m\u001b[0m\u001b[0m\n\u001b[0m\u001b[1;32m   3213\u001b[0m         \u001b[0m_v\u001b[0m \u001b[0;34m=\u001b[0m \u001b[0marg\u001b[0m\u001b[0;34m.\u001b[0m\u001b[0mpop\u001b[0m\u001b[0;34m(\u001b[0m\u001b[0;34m\"opacity\"\u001b[0m\u001b[0;34m,\u001b[0m \u001b[0;32mNone\u001b[0m\u001b[0;34m)\u001b[0m\u001b[0;34m\u001b[0m\u001b[0;34m\u001b[0m\u001b[0m\n\u001b[1;32m   3214\u001b[0m         \u001b[0m_v\u001b[0m \u001b[0;34m=\u001b[0m \u001b[0mopacity\u001b[0m \u001b[0;32mif\u001b[0m \u001b[0mopacity\u001b[0m \u001b[0;32mis\u001b[0m \u001b[0;32mnot\u001b[0m \u001b[0;32mNone\u001b[0m \u001b[0;32melse\u001b[0m \u001b[0m_v\u001b[0m\u001b[0;34m\u001b[0m\u001b[0;34m\u001b[0m\u001b[0m\n\n\u001b[0;32m/opt/homebrew/Caskroom/miniforge/base/envs/main_env/lib/python3.8/site-packages/plotly/basedatatypes.py\u001b[0m in \u001b[0;36m__setitem__\u001b[0;34m(self, prop, value)\u001b[0m\n\u001b[1;32m   4857\u001b[0m                 \u001b[0;31m# ### Handle simple property ###\u001b[0m\u001b[0;34m\u001b[0m\u001b[0;34m\u001b[0m\u001b[0;34m\u001b[0m\u001b[0m\n\u001b[1;32m   4858\u001b[0m                 \u001b[0;32melse\u001b[0m\u001b[0;34m:\u001b[0m\u001b[0;34m\u001b[0m\u001b[0;34m\u001b[0m\u001b[0m\n\u001b[0;32m-> 4859\u001b[0;31m                     \u001b[0mself\u001b[0m\u001b[0;34m.\u001b[0m\u001b[0m_set_prop\u001b[0m\u001b[0;34m(\u001b[0m\u001b[0mprop\u001b[0m\u001b[0;34m,\u001b[0m \u001b[0mvalue\u001b[0m\u001b[0;34m)\u001b[0m\u001b[0;34m\u001b[0m\u001b[0;34m\u001b[0m\u001b[0m\n\u001b[0m\u001b[1;32m   4860\u001b[0m             \u001b[0;32melse\u001b[0m\u001b[0;34m:\u001b[0m\u001b[0;34m\u001b[0m\u001b[0;34m\u001b[0m\u001b[0m\n\u001b[1;32m   4861\u001b[0m                 \u001b[0;31m# Make sure properties dict is initialized\u001b[0m\u001b[0;34m\u001b[0m\u001b[0;34m\u001b[0m\u001b[0;34m\u001b[0m\u001b[0m\n\n\u001b[0;32m/opt/homebrew/Caskroom/miniforge/base/envs/main_env/lib/python3.8/site-packages/plotly/basedatatypes.py\u001b[0m in \u001b[0;36m_set_prop\u001b[0;34m(self, prop, val)\u001b[0m\n\u001b[1;32m   5201\u001b[0m                 \u001b[0;32mreturn\u001b[0m\u001b[0;34m\u001b[0m\u001b[0;34m\u001b[0m\u001b[0m\n\u001b[1;32m   5202\u001b[0m             \u001b[0;32melse\u001b[0m\u001b[0;34m:\u001b[0m\u001b[0;34m\u001b[0m\u001b[0;34m\u001b[0m\u001b[0m\n\u001b[0;32m-> 5203\u001b[0;31m                 \u001b[0;32mraise\u001b[0m \u001b[0merr\u001b[0m\u001b[0;34m\u001b[0m\u001b[0;34m\u001b[0m\u001b[0m\n\u001b[0m\u001b[1;32m   5204\u001b[0m \u001b[0;34m\u001b[0m\u001b[0m\n\u001b[1;32m   5205\u001b[0m         \u001b[0;31m# val is None\u001b[0m\u001b[0;34m\u001b[0m\u001b[0;34m\u001b[0m\u001b[0;34m\u001b[0m\u001b[0m\n\n\u001b[0;32m/opt/homebrew/Caskroom/miniforge/base/envs/main_env/lib/python3.8/site-packages/plotly/basedatatypes.py\u001b[0m in \u001b[0;36m_set_prop\u001b[0;34m(self, prop, val)\u001b[0m\n\u001b[1;32m   5196\u001b[0m \u001b[0;34m\u001b[0m\u001b[0m\n\u001b[1;32m   5197\u001b[0m         \u001b[0;32mtry\u001b[0m\u001b[0;34m:\u001b[0m\u001b[0;34m\u001b[0m\u001b[0;34m\u001b[0m\u001b[0m\n\u001b[0;32m-> 5198\u001b[0;31m             \u001b[0mval\u001b[0m \u001b[0;34m=\u001b[0m \u001b[0mvalidator\u001b[0m\u001b[0;34m.\u001b[0m\u001b[0mvalidate_coerce\u001b[0m\u001b[0;34m(\u001b[0m\u001b[0mval\u001b[0m\u001b[0;34m)\u001b[0m\u001b[0;34m\u001b[0m\u001b[0;34m\u001b[0m\u001b[0m\n\u001b[0m\u001b[1;32m   5199\u001b[0m         \u001b[0;32mexcept\u001b[0m \u001b[0mValueError\u001b[0m \u001b[0;32mas\u001b[0m \u001b[0merr\u001b[0m\u001b[0;34m:\u001b[0m\u001b[0;34m\u001b[0m\u001b[0;34m\u001b[0m\u001b[0m\n\u001b[1;32m   5200\u001b[0m             \u001b[0;32mif\u001b[0m \u001b[0mself\u001b[0m\u001b[0;34m.\u001b[0m\u001b[0m_skip_invalid\u001b[0m\u001b[0;34m:\u001b[0m\u001b[0;34m\u001b[0m\u001b[0;34m\u001b[0m\u001b[0m\n\n\u001b[0;32m/opt/homebrew/Caskroom/miniforge/base/envs/main_env/lib/python3.8/site-packages/_plotly_utils/basevalidators.py\u001b[0m in \u001b[0;36mvalidate_coerce\u001b[0;34m(self, v)\u001b[0m\n\u001b[1;32m   1094\u001b[0m                     \u001b[0mv\u001b[0m \u001b[0;34m=\u001b[0m \u001b[0mstr\u001b[0m\u001b[0;34m(\u001b[0m\u001b[0mv\u001b[0m\u001b[0;34m)\u001b[0m\u001b[0;34m\u001b[0m\u001b[0;34m\u001b[0m\u001b[0m\n\u001b[1;32m   1095\u001b[0m                 \u001b[0;32melse\u001b[0m\u001b[0;34m:\u001b[0m\u001b[0;34m\u001b[0m\u001b[0;34m\u001b[0m\u001b[0m\n\u001b[0;32m-> 1096\u001b[0;31m                     \u001b[0mself\u001b[0m\u001b[0;34m.\u001b[0m\u001b[0mraise_invalid_val\u001b[0m\u001b[0;34m(\u001b[0m\u001b[0mv\u001b[0m\u001b[0;34m)\u001b[0m\u001b[0;34m\u001b[0m\u001b[0;34m\u001b[0m\u001b[0m\n\u001b[0m\u001b[1;32m   1097\u001b[0m \u001b[0;34m\u001b[0m\u001b[0m\n\u001b[1;32m   1098\u001b[0m             \u001b[0;32mif\u001b[0m \u001b[0mself\u001b[0m\u001b[0;34m.\u001b[0m\u001b[0mno_blank\u001b[0m \u001b[0;32mand\u001b[0m \u001b[0mlen\u001b[0m\u001b[0;34m(\u001b[0m\u001b[0mv\u001b[0m\u001b[0;34m)\u001b[0m \u001b[0;34m==\u001b[0m \u001b[0;36m0\u001b[0m\u001b[0;34m:\u001b[0m\u001b[0;34m\u001b[0m\u001b[0;34m\u001b[0m\u001b[0m\n\n\u001b[0;32m/opt/homebrew/Caskroom/miniforge/base/envs/main_env/lib/python3.8/site-packages/_plotly_utils/basevalidators.py\u001b[0m in \u001b[0;36mraise_invalid_val\u001b[0;34m(self, v, inds)\u001b[0m\n\u001b[1;32m    286\u001b[0m                 \u001b[0mname\u001b[0m \u001b[0;34m+=\u001b[0m \u001b[0;34m\"[\"\u001b[0m \u001b[0;34m+\u001b[0m \u001b[0mstr\u001b[0m\u001b[0;34m(\u001b[0m\u001b[0mi\u001b[0m\u001b[0;34m)\u001b[0m \u001b[0;34m+\u001b[0m \u001b[0;34m\"]\"\u001b[0m\u001b[0;34m\u001b[0m\u001b[0;34m\u001b[0m\u001b[0m\n\u001b[1;32m    287\u001b[0m \u001b[0;34m\u001b[0m\u001b[0m\n\u001b[0;32m--> 288\u001b[0;31m         raise ValueError(\n\u001b[0m\u001b[1;32m    289\u001b[0m             \"\"\"\n\u001b[1;32m    290\u001b[0m     \u001b[0mInvalid\u001b[0m \u001b[0mvalue\u001b[0m \u001b[0mof\u001b[0m \u001b[0mtype\u001b[0m \u001b[0;34m{\u001b[0m\u001b[0mtyp\u001b[0m\u001b[0;34m}\u001b[0m \u001b[0mreceived\u001b[0m \u001b[0;32mfor\u001b[0m \u001b[0mthe\u001b[0m \u001b[0;34m'{name}'\u001b[0m \u001b[0mproperty\u001b[0m \u001b[0mof\u001b[0m \u001b[0;34m{\u001b[0m\u001b[0mpname\u001b[0m\u001b[0;34m}\u001b[0m\u001b[0;34m\u001b[0m\u001b[0;34m\u001b[0m\u001b[0m\n\n\u001b[0;31mValueError\u001b[0m: \n    Invalid value of type 'numpy.int64' received for the 'name' property of scatter\n        Received value: 0\n\n    The 'name' property is a string and must be specified as:\n      - A string\n      - A number that will be converted to a string"
}



''')

In [ ]:
asdfg

In [ ]:
df_main.outlier.str.contains('follow_count').value_counts()

In [ ]:
from ipywidgets import interact


In [ ]:
fig.print_grid

In [ ]:
#GPT3 

# Followers vs Follow Count

fig = px.scatter(df_main, x="follow_count", y="follower_count", color="label", trendline="ols")
fig.update_layout(title_text="Followers vs Follow Count",
                  xaxis_title="Follow Count",
                  yaxis_title="Follower Count")
display(fig.show())

# # Comment Emoji Count vs Comment Time Difference

# fig = px.scatter(df_main, x="comment_time_difference", y="comment_emoji_count", color="label", trendline="ols")
# fig.update_layout(title_text="Comment Emoji Count vs Comment Time Difference",
#                   xaxis_title="Comment Time Difference",
#                   yaxis_title="Comment Emoji Count")
# display(fig.show())

# # Post Count vs Video Count

# fig = px.scatter(df_main, x="post_count", y="video_count", color="label", trendline="ols")
# fig.update_layout(title_text="Post Count vs Video Count",
#                   xaxis_title="Post Count",
#                   yaxis_title="Video Count")
# display(fig.show())

# # Highlight Reel Count vs Has Guides

# fig = px.scatter(df_main, x="has_guides", y="highlight_reel_count", color="label", trendline="ols")
# fig.update_layout(title_text="Highlight Reel Count vs Has Guides",
#                   xaxis_title="Has Guides",
#                   yaxis_title="Highlight Reel Count")
# display(fig.show())

# # Has Clips vs Is Private

# fig = px.scatter(df_main, x="is_private", y="has_clips", color="label", trendline="ols")
# fig.update_layout(title_text="Has Clips vs Is Private",
#                   xaxis_title="Is Private",
#                   yaxis_title="Has Clips")
# display(fig.show())

# # Is Embeds Disabled vs Is Joined Recently

# fig = px.scatter(df_main, x="is_joined_recently", y="is_embeds_disabled", color="label", trendline="ols")
# fig.update_layout(title_text="Is Embeds Disabled vs Is Joined Recently",
#                   xaxis_title="Is Joined Recently",
#                   yaxis_title="Is Embeds Disabled")
# display(fig.show())

# # Is Professional Account vs Is Business Account

In [ ]:
# Bivariate Analysis

## Follow Count vs Follower Count

import plotly.express as px

fig = px.scatter(df_main, x="follow_count", y="follower_count", color="label")
fig.update_traces(marker=dict(size=6))
fig.update_layout(title="Follow Count vs Follower Count")
display(fig)

## Comment Emoji Count vs Comment Time Difference

import plotly.express as px

fig = px.scatter(df_main, x="comment_emoji_count", y="comment_time_difference", color="label")
fig.update_traces(marker=dict(size=6))
fig.update_layout(title="Comment Emoji Count vs Comment Time Difference")
display(fig)

## Post Count vs Video Count

import plotly.express as px

fig = px.scatter(df_main, x="post_count", y="video_count", color="label")
fig.update_traces(marker=dict(size=6))
fig.update_layout(title="Post Count vs Video Count")
display(fig)

## Highlight Reel Count vs Has Guides

import plotly.express as px

fig = px.scatter(df_main, x="highlight_reel_count", y="has_guides", color="label")
fig.update_traces(marker=dict(size=6))
fig.update_layout(title="Highlight Reel Count vs Has Guides")
display(fig)

## Has Clips vs Is Private

import plotly.express as px

fig = px.scatter(df_main, x="has_clips", y="is_private", color="label")
fig.update_traces(marker=dict(size=6))
fig.update_layout(title="Has Clips vs Is Private")
display(fig)

## Is Embeds Disabled vs Is Joined Recently

import plotly.express as px

fig = px.scatter(df_main, x="is_embeds_disabled", y="is_joined_recently", color="label")
fig.update_traces(marker=dict(size=6))
fig.update_layout(title="Is Embeds Disabled vs Is Joined Recently")
display(fig)

## Is Professional Account vs Is Business Account

import plotly.express as px

fig = px.scatter(df_main, x="is_professional_account", y="is_business_account", color="label")
fig.update_traces(marker=dict(size=6))
fig.update_layout(title="Is Professional Account vs Is Business Account")
display(fig)

## Should Show Public Contacts vs Posts Days Difference

import plotly.express as px

fig = px.scatter(df_main, x="should_show_public_contacts", y="posts_days_diff", color="label")
fig.update_traces(marker=dict(size=6))
fig.update_layout(title="Should Show Public Contacts vs Posts Days Difference")
display(fig)

## Comment Grams Count vs Biography Word Count

import plotly.express as px

fig = px.scatter(df_main, x="comment_grams_count", y="biography_word_count", color="label")
fig.update_traces(marker=dict(size=6))
fig.update_layout(title="Comment Grams Count vs Biography Word Count")
display(fig)

# Multivariate Analysis

## Follow Count, Follower Count, and Comment Emoji Count

import plotly.express as px

fig = px.scatter_3d(df_main, x="follow_count", y="follower_count", z="comment_emoji_count", color="label")
fig.update_traces(marker=dict(size=6))
fig.update_layout(title="Follow Count, Follower Count, and Comment Emoji Count")
display(fig)

## Post Count, Video Count, and Highlight Reel Count

import plotly.express as px

fig = px.scatter_3d(df_main, x="post_count", y="video_count", z="highlight_reel_count", color="label")
fig.update_traces(marker=dict(size=6))
fig.update_layout(title="Post Count, Video Count, and Highlight Reel Count")
display(fig)

## Has Clips, Is Private, and Is Embeds Disabled

import plotly.express as px

fig = px.scatter_3d(df_main, x="has_clips", y="is_private", z="is_embeds_disabled", color="label")
fig.update_traces(marker=dict(size=6))
fig.update_layout(title="Has Clips, Is Private, and Is Embeds Disabled")
display(fig)

## Is Professional Account, Is Business Account, and Should Show Public Contacts

import plotly.express as px

fig = px.scatter_3d(df_main, x="is_professional_account", y="is_business_account", z="should_show_public_contacts", color="label")
fig.update_traces(marker=dict(size=6))
fig.update_layout(title="Is Professional Account, Is Business Account, and Should Show Public Contacts")
display(fig)

## Posts Days Difference, Comment Grams Count, and Biography Word Count

import plotly.express as px

fig = px.scatter_3d(df_main, x="posts_days_diff", y="comment_grams_count", z="biography_word_count", color="label")
fig.update_traces(marker=dict(size=6))
fig.update_layout(title="Posts Days Difference, Comment Grams Count, and Biography Word Count")
display(fig)

In [ ]:
import numpy as np

biography_bins = np.arange(0, 101, 10)
comment_bins = np.arange(0, 51, 5)

biography_word_counts = df['biography_word_count']
comment_word_counts = df['comment_word_count']

H, xedges, yedges = np.histogram2d(biography_word_counts, comment_word_counts, bins=(biography_bins, comment_bins))

fig = px.imshow(H, x=biography_bins, y=comment_bins, color_continuous_scale='RdBu',
                labels=dict(x='Biography Word Count', y='Comment Word Count', color='Count'))
fig.update_layout(title='Biography Word Count vs. Comment Word Count',
                  xaxis_title='Biography Word Count', yaxis_title='Comment Word Count')
fig.show()


### 2.2 Follow count & follow 

In [ ]:
# df_main.query('comment_time_difference > 74 and label > 0').sort_values('comment_time_difference', ascending=False)[['username', 
#                                                                                                         'post_count', 
#                                                                                                         'comment_time_difference', 
#                                                                                                         'biography', 
#                                                                                                         'label', 
#                                                                                                         'labelling_technique']].head(40)

px.scatter_3d(df_main,
              x='follow_count',
              y='follower_count',
              z='label',
              color='label')

#### 1.1.6 Pairplot

In [ ]:
asdfasdfsafasd

#### 1.1.7

### 2.x Comment likes vs comment time diff

In [ ]:
sub_df = df_main.copy(deep=True)


# sub_df[]

fig = px.scatter(sub_df,
           x='comment_time_difference', 
           y='comment_likes',
           color='label')
# you can be casual and nice to read but remember that the public is from an age of 21 to 100 years old. 
fig.update_layout()

### ?

In [ ]:
percent99 = df_main['follower_count'].quantile(0.9)
sub_df = df_main.query('follower_count < @percent99')


fig = px.histogram(sub_df, 
                   x="follower_count", 
                   nbins=100,
                   color="label",
                   marginal="box", # or violin, rug
                   )

fig.update_layout(barmode='overlay')

In [ ]:
import plotly.figure_factory as ff
import numpy as np

sub_df = df_main.query('follow_count.notna()')


labels = ['0', '1', '3']
hist_data = [sub_df[sub_df['label'] == int(x)]['follow_count'] for x  in labels]

fig = ff.create_distplot(hist_data, labels,
                         bin_size=[200, 200, 200], show_curve=True)

# Add title
fig.update(layout_title_text='Hist and Rug Plot')
fig.show()

# Playground

## Export df_ml

In [ ]:
df_ml = df_main.copy(deep=True)

df_ml['label'].value_counts()
df_ml.isna().sum().tail(40)
s = df_ml.isna().sum().head(50).eq(0)
cols = s[s].index
cols
df_ml.to_sql('ml', con, if_exists='replace', index=False)